In [1]:
import numpy as np
import pandas as pd
import math
pd.set_option('display.max_columns', 500)
pd.options.display.float_format = '{:.2f}'.format

## Summary

This notebook creates two tables. The first is a "business as usual" (BAS) table estimating the number of households by income level by PUMA from 2014 - 2018 for the entire state and imputing those estimates down to the city and unincorporated county level. 

The second is a "meeting regional housing needs" (needs) table that adds 1/8 of RHNA targets for each income category in jurisdictions in the Bay Area that fall short of those targets and draws those households from cities and counties in the greater Bay Area commute shed based on weights of the number of people who have moved to those locations by county.

## Outline
### Part A. Create "Business-as-Usual" Scenario Dataframe
1. Import each year's total households by puma and merge across years
2. Impute estimates down to the city level
3. Regroup CDP and Unincorporated PUMAs into "Unincorporated Counties"
4. Regroup city and unincorporated county dfs together and drop duplicates 

### Part B. Create "Meeting Regional Housing Needs" Scenario
1. Copy BAS scenario df and import RHNA allocations by city and county
2. Calculate difference between RHNA allocations and changes in household counts over time period
3. Bring in move data and create weights for reallocation of hhs
4. Reallocate hhs using move weights

## Part 1. Import each year's total households by puma and merge across years

In [2]:
#import household counts by income group by PUMA from each year
col_18 = ["PUMA","18_ELI_hh_count","18_VLI_hh_count","18_LI_hh_count","18_MoI_hh_count","18_HI_hh_count"]
y18_df=pd.read_csv("2018 Analysis/2018_ppl_hh_puma_counts.csv", delimiter=",",usecols=col_18)
col_17 = ["PUMA","17_ELI_hh_count","17_VLI_hh_count","17_LI_hh_count","17_MoI_hh_count","17_HI_hh_count"]
y17_df=pd.read_csv("2017 Analysis/2017_ppl_hh_puma_counts.csv", delimiter=",",usecols=col_17)
col_16 = ["PUMA","16_ELI_hh_count","16_VLI_hh_count","16_LI_hh_count","16_MoI_hh_count","16_HI_hh_count"]
y16_df=pd.read_csv("2016 Analysis/2016_ppl_hh_puma_counts.csv", delimiter=",",usecols=col_16)
col_15 = ["PUMA","15_ELI_hh_count","15_VLI_hh_count","15_LI_hh_count","15_MoI_hh_count","15_HI_hh_count"]
y15_df=pd.read_csv("2015 Analysis/2015_ppl_hh_puma_counts.csv", delimiter=",",usecols=col_15)
col_14 = ["PUMA","14_ELI_hh_count","14_VLI_hh_count","14_LI_hh_count","14_MoI_hh_count","14_HI_hh_count"]
y14_df=pd.read_csv("2014 Analysis/2014_ppl_hh_puma_counts.csv", delimiter=",",usecols=col_14)

In [3]:
# merge aggregated dataframes from each year
totals_df = y14_df.merge(y15_df,how='left', left_on = "PUMA",right_on = "PUMA")
totals_df = totals_df.merge(y16_df,how='left', left_on = "PUMA",right_on = "PUMA")
totals_df = totals_df.merge(y17_df,how='left', left_on = "PUMA",right_on = "PUMA")
totals_df = totals_df.merge(y18_df,how='left', left_on = "PUMA",right_on = "PUMA")
totals_df

PUMA  14_ELI_hh_count  14_VLI_hh_count  14_LI_hh_count  14_MoI_hh_count  \
0      101         11278.00          4381.00         3939.00          9228.00   
1      102         19067.00         12644.00         9821.00         13194.00   
2      103          5584.00          5033.00         3449.00         11307.00   
3      104         12352.00          8142.00         5701.00          8693.00   
4      105          8366.00          8447.00         7826.00         16029.00   
5      106          8004.00          7084.00         5405.00         13080.00   
6      107          7538.00          7708.00         5790.00         13704.00   
7      108          4638.00          3100.00         4150.00         10513.00   
8      109          6135.00          5167.00         6548.00         15131.00   
9      110          5003.00          6835.00         5925.00         16604.00   
10     300         11325.00         10202.00        14568.00         17254.00   
11     701          7577.00          6433.00         6207.00          6928.00   
12     702          5694.00          6139.00         8141.00          8383.00   
13    1100          6648.00          5987.00         9201.00          7953.00   
14    1301         11301.00          8060.00         6003.00          8610.00   
15    1302          5950.00          3909.00         4778.00         12015.00   
16    1303          6778.00          4784.00         6883.00         12793.00   
17    1304          4295.00          3251.00         4955.00         10006.00   
18    1305          1833.00          1908.00         3239.00          7164.00   
19    1306          3817.00          3821.00         4763.00         11003.00   
20    1307          8346.00          4208.00         7574.00          9508.00   
21    1308          7927.00          4252.00         6304.00          7981.00   
22    1309          3232.00          4001.00         4672.00         10074.00   
23    1500          8370.00          7736.00         7123.00          7793.00   
24    1700          5621.00          8938.00         9385.00         12289.00   
25    1901          7916.00          7125.00         8129.00          6817.00   
26    1902          7179.00          6083.00         7881.00         11693.00   
27    1903          7609.00          5417.00         6873.00          4757.00   
28    1904         12881.00          8830.00        11423.00          7179.00   
29    1905          4907.00          4819.00         5773.00          5424.00   
..     ...              ...              ...             ...              ...   
235   8509          7851.00          6156.00         8496.00          6747.00   
236   8510         10686.00          6936.00         9814.00          7520.00   
237   8511          3931.00          4402.00         6082.00          6507.00   
238   8512          3140.00          3580.00         5481.00          8134.00   
239   8513          2923.00          4057.00         5242.00          6497.00   
240   8514          6825.00          3788.00         6700.00          4633.00   
241   8701          7787.00          7209.00        10066.00          5787.00   
242   8702          9760.00          7522.00         7839.00          4321.00   
243   8900          8895.00          9630.00        11446.00         12727.00   
244   9501          8700.00          6775.00         7728.00         11048.00   
245   9502          5481.00          4273.00         8618.00         10499.00   
246   9503          6059.00          5985.00         7118.00         10002.00   
247   9701          9058.00          7596.00        11009.00         14632.00   
248   9702          6273.00          3979.00         7439.00          9581.00   
249   9703         12031.00          8842.00        13454.00         12149.00   
250   9901          3412.00          4742.00         6708.00          7987.00   
251   9902          7679.00          4363.00         6948.00          6699.00   
252   9903          7543.00          

In [4]:
# aggregate ELI and VLI for each year, then drop ELI column
totals_df["14_VLI_hh_count"]=totals_df["14_ELI_hh_count"]+totals_df["14_VLI_hh_count"]
totals_df.drop('14_ELI_hh_count', axis=1, inplace=True)
totals_df["15_VLI_hh_count"]=totals_df["15_ELI_hh_count"]+totals_df["15_VLI_hh_count"]
totals_df.drop('15_ELI_hh_count', axis=1, inplace=True)
totals_df["16_VLI_hh_count"]=totals_df["16_ELI_hh_count"]+totals_df["16_VLI_hh_count"]
totals_df.drop('16_ELI_hh_count', axis=1, inplace=True)
totals_df["17_VLI_hh_count"]=totals_df["17_ELI_hh_count"]+totals_df["17_VLI_hh_count"]
totals_df.drop('17_ELI_hh_count', axis=1, inplace=True)
totals_df["18_VLI_hh_count"]=totals_df["18_ELI_hh_count"]+totals_df["18_VLI_hh_count"]
totals_df.drop('18_ELI_hh_count', axis=1, inplace=True)
totals_df

PUMA  14_VLI_hh_count  14_LI_hh_count  14_MoI_hh_count  14_HI_hh_count  \
0      101         15659.00         3939.00          9228.00        21760.00   
1      102         31711.00         9821.00         13194.00        18026.00   
2      103         10617.00         3449.00         11307.00        28070.00   
3      104         20494.00         5701.00          8693.00         4722.00   
4      105         16813.00         7826.00         16029.00        24327.00   
5      106         15088.00         5405.00         13080.00        13695.00   
6      107         15246.00         5790.00         13704.00        14185.00   
7      108          7738.00         4150.00         10513.00        17855.00   
8      109         11302.00         6548.00         15131.00        32451.00   
9      110         11838.00         5925.00         16604.00        44089.00   
10     300         21527.00        14568.00         17254.00        20595.00   
11     701         14010.00         6207.00          6928.00        17737.00   
12     702         11833.00         8141.00          8383.00        11806.00   
13    1100         12635.00         9201.00          7953.00        16270.00   
14    1301         19361.00         6003.00          8610.00         6307.00   
15    1302          9859.00         4778.00         12015.00        19415.00   
16    1303         11562.00         6883.00         12793.00        17047.00   
17    1304          7546.00         4955.00         10006.00        28780.00   
18    1305          3741.00         3239.00          7164.00        28970.00   
19    1306          7638.00         4763.00         11003.00        22683.00   
20    1307         12554.00         7574.00          9508.00         9761.00   
21    1308         12179.00         6304.00          7981.00         9994.00   
22    1309          7233.00         4672.00         10074.00        13436.00   
23    1500         16106.00         7123.00          7793.00        18680.00   
24    1700         14559.00         9385.00         12289.00        29506.00   
25    1901         15041.00         8129.00          6817.00        10066.00   
26    1902         13262.00         7881.00         11693.00        34490.00   
27    1903         13026.00         6873.00          4757.00         6497.00   
28    1904         21711.00        11423.00          7179.00        14297.00   
29    1905          9726.00         5773.00          5424.00         6945.00   
..     ...              ...             ...              ...             ...   
235   8509         14007.00         8496.00          6747.00        15617.00   
236   8510         17622.00         9814.00          7520.00        17676.00   
237   8511          8333.00         6082.00          6507.00        15656.00   
238   8512          6720.00         5481.00          8134.00        16908.00   
239   8513          6980.00         5242.00          6497.00        11312.00   
240   8514         10613.00         6700.00          4633.00         2848.00   
241   8701         14996.00        10066.00          5787.00        16798.00   
242   8702         17282.00         7839.00          4321.00        18539.00   
243   8900         18525.00        11446.00         12727.00        25844.00   
244   9501         15475.00         7728.00         11048.00        18311.00   
245   9502          9754.00         8618.00         10499.00        17591.00   
246   9503         12044.00         7118.00         10002.00        16802.00   
247   9701         16654.00        11009.00         14632.00        33415.00   
248   9702         10252.00         7439.00          9581.00        18111.00   
249   9703         20873.00        13454.00         12149.00        23162.00   
250   9901          8154.00         6708.00          7987.00        10571.00   
251   9902         12042.00         6948.00          6699.00        12648.00   
252   9903         13379.00        10363.00          9440.00        23735.00   
253   

## Part 2. Impute estimates down to the city level

In [5]:
#import crosswalk file
crosswalk_df = pd.read_csv("puma_place_crosswalk.csv", delimiter=",",encoding='latin1')

#adjust "Unincorporated 3300" weight down to only include Mendocino County portion
mask = (crosswalk_df.Place=="Unincorporated_3300")
column_name = "puma_to_place_factor"
fill = 0.324290664
crosswalk_df.loc[mask, column_name]=fill
crosswalk_df

PUMA                                   Place  puma_to_place_factor  \
0       101                         Albany city, CA                  0.14   
1       101                       Berkeley city, CA                  0.86   
2       102                     Emeryville city, CA                  0.09   
3       102                        Oakland city, CA                  0.92   
4       103                        Oakland city, CA                  0.93   
5       103                       Piedmont city, CA                  0.07   
6       104                        Oakland city, CA                  1.00   
7       104                    San Leandro city, CA                  0.00   
8       105                        Alameda city, CA                  0.49   
9       105                   Castro Valley CDP, CA                  0.01   
10      105                        Oakland city, CA                  0.02   
11      105                    San Leandro city, CA                  0.49   
12      106                         Ashland CDP, CA                  0.16   
13      106                   Castro Valley CDP, CA                  0.44   
14      106                      Cherryland CDP, CA                  0.09   
15      106                        Fairview CDP, CA                  0.05   
16      106                        Hayward city, CA                  0.07   
17      106                    San Leandro city, CA                  0.00   
18      106                     San Lorenzo CDP, CA                  0.16   
19      106                      Unincorporated_106                  0.03   
20      107                   Castro Valley CDP, CA                  0.02   
21      107                      Cherryland CDP, CA                  0.01   
22      107                        Fairview CDP, CA                  0.03   
23      107                        Hayward city, CA                  0.93   
24      107                           Sunol CDP, CA                  0.00   
25      107                     Union City city, CA                  0.01   
26      107                      Unincorporated_107                  0.01   
27      108                        Fremont city, CA                  0.19   
28      108                         Newark city, CA                  0.32   
29      108                     Union City city, CA                  0.49   
...     ...                                     ...                   ...   
2138  11105                       Moorpark city, CA                  0.06   
2139  11105                        Oak View CDP, CA                  0.04   
2140  11105                           Ojai city, CA                  0.08   
2141  11105                         Oxnard city, CA                  0.01   
2142  11105                            Piru CDP, CA                  0.01   
2143  11105     San Buenaventura (Ventura) city, CA                  0.00   
2144  11105                    Santa Paula city, CA                  0.22   
2145  11105                    Simi Valley city, CA                  0.11   
2146  11105                    Unincorporated_11105                  0.20   
2147  11106                      Camarillo city, CA                  0.58   
2148  11106                   Lake Sherwood CDP, CA                  0.01   
2149  11106                       Moorpark city, CA                  0.19   
2150  11106                         Oxnard city, CA                  0.07   
2151  11106               Santa Rosa Valley CDP, CA                  0.03   
2152  11106                  Thousand Oaks city, CA                  0.00   
2153  11106                    Unincorporated_11106                  0.12   
2154  11300                      Clarksburg CDP, CA                  0.00   
2155  11300                          Davis city, CA                  0.34   
2156  11300                        Dunnigan CDP, CA                  0.01   
2157  11300                         Esparto CDP, CA                  0.01   
215

In [6]:
#merge with crosswalk file
puma_place_df=totals_df.merge(crosswalk_df,how='left', on="PUMA")
puma_place_df

PUMA  14_VLI_hh_count  14_LI_hh_count  14_MoI_hh_count  14_HI_hh_count  \
0       101         15659.00         3939.00          9228.00        21760.00   
1       101         15659.00         3939.00          9228.00        21760.00   
2       102         31711.00         9821.00         13194.00        18026.00   
3       102         31711.00         9821.00         13194.00        18026.00   
4       103         10617.00         3449.00         11307.00        28070.00   
5       103         10617.00         3449.00         11307.00        28070.00   
6       104         20494.00         5701.00          8693.00         4722.00   
7       104         20494.00         5701.00          8693.00         4722.00   
8       105         16813.00         7826.00         16029.00        24327.00   
9       105         16813.00         7826.00         16029.00        24327.00   
10      105         16813.00         7826.00         16029.00        24327.00   
11      105         16813.00         7826.00         16029.00        24327.00   
12      106         15088.00         5405.00         13080.00        13695.00   
13      106         15088.00         5405.00         13080.00        13695.00   
14      106         15088.00         5405.00         13080.00        13695.00   
15      106         15088.00         5405.00         13080.00        13695.00   
16      106         15088.00         5405.00         13080.00        13695.00   
17      106         15088.00         5405.00         13080.00        13695.00   
18      106         15088.00         5405.00         13080.00        13695.00   
19      106         15088.00         5405.00         13080.00        13695.00   
20      107         15246.00         5790.00         13704.00        14185.00   
21      107         15246.00         5790.00         13704.00        14185.00   
22      107         15246.00         5790.00         13704.00        14185.00   
23      107         15246.00         5790.00         13704.00        14185.00   
24      107         15246.00         5790.00         13704.00        14185.00   
25      107         15246.00         5790.00         13704.00        14185.00   
26      107         15246.00         5790.00         13704.00        14185.00   
27      108          7738.00         4150.00         10513.00        17855.00   
28      108          7738.00         4150.00         10513.00        17855.00   
29      108          7738.00         4150.00         10513.00        17855.00   
...     ...              ...             ...              ...             ...   
2138  11105         11869.00         7137.00          8265.00        10023.00   
2139  11105         11869.00         7137.00          8265.00        10023.00   
2140  11105         11869.00         7137.00          8265.00        10023.00   
2141  11105         11869.00         7137.00          8265.00        10023.00   
2142  11105         11869.00         7137.00          8265.00        10023.00   
2143  11105         11869.00         7137.00          8265.00        10023.00   
2144  11105         11869.00         7137.00          8265.00        10023.00   
2145  11105         11869.00         7137.00          8265.00        10023.00   
2146  11105         11869.00         7137.00          8265.00        10023.00   
2147  11106          6832.00         6021.00          8396.00        19396.00   
2148  11106          6832.00         6021.00          8396.00        19396.00   
2149  11106          6832.00         6021.00          8396.00        19396.00   
2150  11106          6832.00         6021.00          8396.00        19396.00   
2151  11106          6832.00         6021.00          8396.00        19396.00   
2152  11106          6832.00         6021.00          8396.00        19396.00   
2153  11106          6832.00         6021.00          8396.00        19396.00   
2154  11300         24300.00        10260.00         11735.00        25704.00   
2155  11300         24300.00        10

In [7]:
county_col = ["PUMA","county1"]
county_crosswalk_df=pd.read_csv("PUMA_County_Crosswalk_v2.csv", delimiter=",",usecols=county_col)
puma_place_df = puma_place_df.merge(county_crosswalk_df,how='left', left_on = "PUMA",right_on = "PUMA")
puma_place_df['County'] = puma_place_df['county1'].str.replace(r' CA', '')
puma_place_df.drop('county1', axis=1, inplace=True)
puma_place_df

PUMA  14_VLI_hh_count  14_LI_hh_count  14_MoI_hh_count  14_HI_hh_count  \
0       101         15659.00         3939.00          9228.00        21760.00   
1       101         15659.00         3939.00          9228.00        21760.00   
2       102         31711.00         9821.00         13194.00        18026.00   
3       102         31711.00         9821.00         13194.00        18026.00   
4       103         10617.00         3449.00         11307.00        28070.00   
5       103         10617.00         3449.00         11307.00        28070.00   
6       104         20494.00         5701.00          8693.00         4722.00   
7       104         20494.00         5701.00          8693.00         4722.00   
8       105         16813.00         7826.00         16029.00        24327.00   
9       105         16813.00         7826.00         16029.00        24327.00   
10      105         16813.00         7826.00         16029.00        24327.00   
11      105         16813.00         7826.00         16029.00        24327.00   
12      106         15088.00         5405.00         13080.00        13695.00   
13      106         15088.00         5405.00         13080.00        13695.00   
14      106         15088.00         5405.00         13080.00        13695.00   
15      106         15088.00         5405.00         13080.00        13695.00   
16      106         15088.00         5405.00         13080.00        13695.00   
17      106         15088.00         5405.00         13080.00        13695.00   
18      106         15088.00         5405.00         13080.00        13695.00   
19      106         15088.00         5405.00         13080.00        13695.00   
20      107         15246.00         5790.00         13704.00        14185.00   
21      107         15246.00         5790.00         13704.00        14185.00   
22      107         15246.00         5790.00         13704.00        14185.00   
23      107         15246.00         5790.00         13704.00        14185.00   
24      107         15246.00         5790.00         13704.00        14185.00   
25      107         15246.00         5790.00         13704.00        14185.00   
26      107         15246.00         5790.00         13704.00        14185.00   
27      108          7738.00         4150.00         10513.00        17855.00   
28      108          7738.00         4150.00         10513.00        17855.00   
29      108          7738.00         4150.00         10513.00        17855.00   
...     ...              ...             ...              ...             ...   
2138  11105         11869.00         7137.00          8265.00        10023.00   
2139  11105         11869.00         7137.00          8265.00        10023.00   
2140  11105         11869.00         7137.00          8265.00        10023.00   
2141  11105         11869.00         7137.00          8265.00        10023.00   
2142  11105         11869.00         7137.00          8265.00        10023.00   
2143  11105         11869.00         7137.00          8265.00        10023.00   
2144  11105         11869.00         7137.00          8265.00        10023.00   
2145  11105         11869.00         7137.00          8265.00        10023.00   
2146  11105         11869.00         7137.00          8265.00        10023.00   
2147  11106          6832.00         6021.00          8396.00        19396.00   
2148  11106          6832.00         6021.00          8396.00        19396.00   
2149  11106          6832.00         6021.00          8396.00        19396.00   
2150  11106          6832.00         6021.00          8396.00        19396.00   
2151  11106          6832.00         6021.00          8396.00        19396.00   
2152  11106          6832.00         6021.00          8396.00        19396.00   
2153  11106          6832.00         6021.00          8396.00        19396.00   
2154  11300         24300.00        10260.00         11735.00        25704.00   
2155  11300         24300.00        10

In [8]:
# create a reference dataframe for county names and dummy variables
ref_df=puma_place_df[["PUMA","County","Place"]].copy()
ref_df

PUMA   County                                   Place
0       101  Alameda                         Albany city, CA
1       101  Alameda                       Berkeley city, CA
2       102  Alameda                     Emeryville city, CA
3       102  Alameda                        Oakland city, CA
4       103  Alameda                        Oakland city, CA
5       103  Alameda                       Piedmont city, CA
6       104  Alameda                        Oakland city, CA
7       104  Alameda                    San Leandro city, CA
8       105  Alameda                        Alameda city, CA
9       105  Alameda                   Castro Valley CDP, CA
10      105  Alameda                        Oakland city, CA
11      105  Alameda                    San Leandro city, CA
12      106  Alameda                         Ashland CDP, CA
13      106  Alameda                   Castro Valley CDP, CA
14      106  Alameda                      Cherryland CDP, CA
15      106  Alameda                        Fairview CDP, CA
16      106  Alameda                        Hayward city, CA
17      106  Alameda                    San Leandro city, CA
18      106  Alameda                     San Lorenzo CDP, CA
19      106  Alameda                      Unincorporated_106
20      107  Alameda                   Castro Valley CDP, CA
21      107  Alameda                      Cherryland CDP, CA
22      107  Alameda                        Fairview CDP, CA
23      107  Alameda                        Hayward city, CA
24      107  Alameda                           Sunol CDP, CA
25      107  Alameda                     Union City city, CA
26      107  Alameda                      Unincorporated_107
27      108  Alameda                        Fremont city, CA
28      108  Alameda                         Newark city, CA
29      108  Alameda                     Union City city, CA
...     ...      ...                                     ...
2138  11105  Ventura                       Moorpark city, CA
2139  11105  Ventura                        Oak View CDP, CA
2140  11105  Ventura                           Ojai city, CA
2141  11105  Ventura                         Oxnard city, CA
2142  11105  Ventura                            Piru CDP, CA
2143  11105  Ventura     San Buenaventura (Ventura) city, CA
2144  11105  Ventura                    Santa Paula city, CA
2145  11105  Ventura                    Simi Valley city, CA
2146  11105  Ventura                    Unincorporated_11105
2147  11106  Ventura                      Camarillo city, CA
2148  11106  Ventura                   Lake Sherwood CDP, CA
2149  11106  Ventura                       Moorpark city, CA
2150  11106  Ventura                         Oxnard city, CA
2151  11106  Ventura               Santa Rosa Valley CDP, CA
2152  11106  Ventura                  Thousand Oaks city, CA
2153  11106  Ventura                    Unincorporated_11106
2154  11300     Yolo                      Clarksburg CDP, CA
2155  11300     Yolo                          Davis city, CA
2156  11300     Yolo                        Dunnigan CDP, CA
2157  11300     Yolo                         Esparto CDP, CA
2158  11300     Yolo                          Guinda CDP, CA
2159  11300     Yolo                 Knights Landing CDP, CA
2160  11300     Yolo                         Madison CDP, CA
2161  11300     Yolo                  Monument Hills CDP, CA
2162  11300     Yolo  University of California Davis CDP, CA
2163  11300     Yolo                West Sacramento city, CA
2164  11300     Yolo                        Winters city, CA
2165  11300     Yolo                       Woodland city, CA
2166  11300     Yolo                            Yolo CDP, CA
2167  11300     Yolo                    Unincorporated_11300

[2168 rows x 3 columns]

In [9]:
#multiply each column by the weighting factor for that geography
puma_place_df["14_VLI_hh_count"]=puma_place_df["14_VLI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["14_LI_hh_count"]=puma_place_df["14_LI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["14_MoI_hh_count"]=puma_place_df["14_MoI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["14_HI_hh_count"]=puma_place_df["14_HI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["15_VLI_hh_count"]=puma_place_df["15_VLI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["15_LI_hh_count"]=puma_place_df["15_LI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["15_MoI_hh_count"]=puma_place_df["15_MoI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["15_HI_hh_count"]=puma_place_df["15_HI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["16_VLI_hh_count"]=puma_place_df["16_VLI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["16_LI_hh_count"]=puma_place_df["16_LI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["16_MoI_hh_count"]=puma_place_df["16_MoI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["16_HI_hh_count"]=puma_place_df["16_HI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["17_VLI_hh_count"]=puma_place_df["17_VLI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["17_LI_hh_count"]=puma_place_df["17_LI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["17_MoI_hh_count"]=puma_place_df["17_MoI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["17_HI_hh_count"]=puma_place_df["17_HI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["18_VLI_hh_count"]=puma_place_df["18_VLI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["18_LI_hh_count"]=puma_place_df["18_LI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["18_MoI_hh_count"]=puma_place_df["18_MoI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df["18_HI_hh_count"]=puma_place_df["18_HI_hh_count"]*puma_place_df["puma_to_place_factor"]
puma_place_df

PUMA  14_VLI_hh_count  14_LI_hh_count  14_MoI_hh_count  14_HI_hh_count  \
0       101          2160.94          543.58          1273.46         3002.88   
1       101         13498.06         3395.42          7954.54        18757.12   
2       102          2695.44          834.79          1121.49         1532.21   
3       102         29015.57         8986.22         12072.51        16493.79   
4       103          9905.66         3217.92         10549.43        26189.31   
5       103           711.34          231.08           757.57         1880.69   
6       104         20494.00         5701.00          8693.00         4722.00   
7       104             0.00            0.00             0.00            0.00   
8       105          8204.74         3819.09          7822.15        11871.58   
9       105           134.50           62.61           128.23          194.62   
10      105           269.01          125.22           256.46          389.23   
11      105          8204.74         3819.09          7822.15        11871.58   
12      106          2368.82          848.59          2053.56         2150.12   
13      106          6668.90         2389.01          5781.36         6053.19   
14      106          1403.18          502.67          1216.44         1273.64   
15      106           724.22          259.44           627.84          657.36   
16      106          1116.51          399.97           967.92         1013.43   
17      106            15.09            5.41            13.08           13.70   
18      106          2353.73          843.18          2040.48         2136.42   
19      106           437.55          156.74           379.32          397.15   
20      107           350.66          133.17           315.19          326.25   
21      107           121.97           46.32           109.63          113.48   
22      107           396.40          150.54           356.30          368.81   
23      107         14178.78         5384.70         12744.72        13192.05   
24      107             0.00            0.00             0.00            0.00   
25      107           121.97           46.32           109.63          113.48   
26      107            76.23           28.95            68.52           70.92   
27      108          1462.48          784.35          1986.96         3374.59   
28      108          2452.95         1315.55          3332.62         5660.03   
29      108          3814.83         2045.95          5182.91         8802.51   
...     ...              ...             ...              ...             ...   
2138  11105           676.53          406.81           471.11          571.31   
2139  11105           451.02          271.21           314.07          380.87   
2140  11105           997.00          599.51           694.26          841.93   
2141  11105           154.30           92.78           107.45          130.30   
2142  11105           166.17           99.92           115.71          140.32   
2143  11105             0.00            0.00             0.00            0.00   
2144  11105          2575.57         1548.73          1793.50         2174.99   
2145  11105          1293.72          777.93           900.88         1092.51   
2146  11105          2433.14         1463.08          1694.32         2054.71   
2147  11106          3996.72         3522.28          4911.66        11346.66   
2148  11106            61.49           54.19            75.56          174.56   
2149  11106          1311.74         1156.03          1612.03         3724.03   
2150  11106           485.07          427.49           596.12         1377.12   
2151  11106           177.63          156.55           218.30          504.30   
2152  11106             0.00            0.00             0.00            0.00   
2153  11106           806.18          710.48           990.73         2288.73   
2154  11300            48.60           20.52            23.47           51.41   
2155  11300          8383.50         3

## Part 3. Group CDP and Unincorporated PUMAs into "Unincorporated Counties"

In [10]:
# create separate unincorporated df
unin_df = puma_place_df[(puma_place_df.Place.str.contains("CDP"))|(puma_place_df.Place.str.contains("Unincorporated"))].copy()
unin_df

PUMA  14_VLI_hh_count  14_LI_hh_count  14_MoI_hh_count  14_HI_hh_count  \
9       105           134.50           62.61           128.23          194.62   
12      106          2368.82          848.59          2053.56         2150.12   
13      106          6668.90         2389.01          5781.36         6053.19   
14      106          1403.18          502.67          1216.44         1273.64   
15      106           724.22          259.44           627.84          657.36   
18      106          2353.73          843.18          2040.48         2136.42   
19      106           437.55          156.74           379.32          397.15   
20      107           350.66          133.17           315.19          326.25   
21      107           121.97           46.32           109.63          113.48   
22      107           396.40          150.54           356.30          368.81   
24      107             0.00            0.00             0.00            0.00   
26      107            76.23           28.95            68.52           70.92   
30      108             0.00            0.00             0.00            0.00   
36      110            59.19           29.62            83.02          220.44   
37      110           236.76          118.50           332.08          881.78   
38      300            21.53           14.57            17.25           20.59   
41      300           947.19          640.99           759.18          906.18   
42      300             0.00            0.00             0.00            0.00   
43      300            64.58           43.70            51.76           61.79   
44      300           107.64           72.84            86.27          102.98   
45      300            21.53           14.57            17.25           20.59   
46      300            21.53           14.57            17.25           20.59   
47      300           172.22          116.54           138.03          164.76   
49      300            86.11           58.27            69.02           82.38   
50      300            64.58           43.70            51.76           61.79   
51      300           322.90          218.52           258.81          308.93   
52      300             0.00            0.00             0.00            0.00   
53      300            43.05           29.14            34.51           41.19   
54      300            86.11           58.27            69.02           82.38   
55      300            64.58           43.70            51.76           61.79   
...     ...              ...             ...              ...             ...   
2117  11101            49.35           37.93            47.07           97.56   
2118  11102           110.82           74.90           128.94          333.82   
2119  11102           166.23          112.36           193.41          500.72   
2120  11102            36.94           24.97            42.98          111.27   
2121  11102           868.09          586.75          1010.03         2614.89   
2124  11102           230.88          156.05           268.62          695.45   
2125  11103           629.24          379.75           347.85          365.50   
2128  11103             0.00            0.00             0.00            0.00   
2129  11104             0.00            0.00             0.00            0.00   
2132  11104            68.54           44.23            69.62           96.04   
2133  11104            91.39           58.98            92.82          128.06   
2134  11105           498.50          299.75           347.13          420.97   
2136  11105           415.42          249.80           289.28          350.81   
2137  11105           890.17          535.27           619.88          751.73   
2139  11105           451.02          271.21           314.07          380.87   
2142  11105           166.17           99.92           115.71          140.32   
2146  11105          2433.14         1463.08          1694.32         2054.71   
2148  11106            61.49          

In [11]:
#reassign unicorporated parts of Mendocino County from Lake County
mask = (unin_df.Place=="Albion CDP, CA")|(unin_df.Place=="Anchor Bay CDP, CA")|(unin_df.Place=="Boonville CDP, CA")|(unin_df.Place=="Brooktrails CDP, CA")|(unin_df.Place=="Calpella CDP, CA")|(unin_df.Place=="Caspar CDP, CA")|(unin_df.Place=="Cleone CDP, CA")|(unin_df.Place=="Comptche CDP, CA")|(unin_df.Place=="Covelo CDP, CA")|(unin_df.Place=="Hopland CDP, CA")|(unin_df.Place=="Laytonville CDP, CA")|(unin_df.Place=="Leggett CDP, CA")|(unin_df.Place=="Little River CDP, CA")|(unin_df.Place=="Manchester CDP, CA")|(unin_df.Place=="Mendocino CDP, CA")|(unin_df.Place=="Philo CDP, CA")|(unin_df.Place=="Potter Valley CDP, CA")|(unin_df.Place=="Redwood Valley CDP, CA")|(unin_df.Place=="Talmage CDP, CA")|(unin_df.Place=="Talmage CDP, CA")|(unin_df.Place=="Unincorporated_3300")
column_name = "County"
fill = "Mendocino"
unin_df.loc[mask, column_name]=fill

In [12]:
# group by county
regrouped_unin_df = unin_df.groupby("County").sum()
regrouped_unin_df2 = regrouped_unin_df.reset_index()

In [13]:
# add Place column with County name + "Unincorporated_"
regrouped_unin_df2["Place"]="Unincorporated_"+regrouped_unin_df2.County
regrouped_unin_df2.drop('PUMA', axis=1, inplace=True)
regrouped_unin_df2.drop('puma_to_place_factor', axis=1, inplace=True)
regrouped_unin_df2.drop('place_code', axis=1, inplace=True)
regrouped_unin_df2

County  14_VLI_hh_count  14_LI_hh_count  14_MoI_hh_count  \
0           Alameda         15332.11         5569.34         13491.98   
1            Alpine         17286.18        11698.10         13854.96   
2             Butte          9534.59         5780.71          6074.33   
3            Colusa          8541.26         6219.88          5376.23   
4      Contra Costa         12910.13         7390.29         14454.25   
5         Del Norte         11628.53         5142.81          5626.55   
6         El Dorado         11297.78         7282.76          9536.26   
7            Fresno         18737.66         9815.83          9271.50   
8          Humboldt          9143.88         5174.45          5738.04   
9          Imperial          3955.03         1897.63          2065.53   
10             Kern         30412.24        19161.87         16240.04   
11            Kings          2888.88         1523.14          2150.90   
12             Lake          4320.90         2459.26          2020.70   
13      Los Angeles         99455.52        54978.62         16949.53   
14           Madera          6253.68         4576.38          5257.41   
15            Marin          6646.97         4722.67          3405.90   
16        Mendocino          8289.18         4717.82          3876.50   
17           Merced          7100.80         5278.60          5123.77   
18         Monterey         10013.91         6733.10          6920.53   
19             Napa          3008.29         1831.28          2109.48   
20           Nevada          5587.56         4681.19          5353.16   
21           Orange          8753.09         5191.27          5183.47   
22           Placer          9115.88         7346.68          6332.88   
23        Riverside         38820.03        26948.29         23739.06   
24       Sacramento         67003.93        40025.02         36107.24   
25   San Bernardino         31043.71        16242.87         16670.96   
26        San Diego         39134.36        29557.68         24108.55   
27      San Joaquin         13336.49         8347.86          8081.99   
28  San Luis Obispo         11198.78         6834.22          7761.06   
29        San Mateo          4302.13         2976.73          2295.53   
30    Santa Barbara         13433.21         7547.50          6206.13   
31      Santa Clara          7071.46         4355.54          5077.33   
32       Santa Cruz         17499.34         9922.04          5614.18   
33           Shasta          7261.80         4486.83          4988.98   
34           Solano          1835.77         1156.47          1571.21   
35           Sonoma         14317.39         9488.09         11780.67   
36       Stanislaus          8661.90         6427.55          6586.31   
37           Sutter          7197.93         4980.83          5320.93   
38           Tulare         14107.12         8909.86          6223.49   
39          Ventura          8241.67         5385.68          6952.62   
40             Yolo          2721.60         1149.12          1314.32   

    14_HI_hh_count  15_VLI_hh_count  15_LI_hh_count  15_MoI_hh_count  \
0         14844.19         11326.94         8670.08         10133.76   
1         16537.78         19351.50        11385.74         14492.54   
2         10366.12          9025.74         5499.12          6043.29   
3         10998.52          9183.46         5577.68          5759.52   
4         25402.32         13535.29         7306.09         12601.40   
5         13486.96          9923.17         6194.76          5843.87   
6         22896.66         10293.64         5705.15          9221.98   
7         18453.65         17231.95        10348.43         10233.11   
8          9283.54          7948.25         5443.82          5847.34   
9          3083.31          4085.84         1707.13          1804.67   
10        33794.98         28416.13        18278.81         15733.38   
11         3226.36          2625.50         1812.01          1457.06   
12        

In [14]:
#drop unincorporated areas from original df
mask = (~puma_place_df["Place"].str.contains("CDP"))&(~puma_place_df["Place"].str.contains("Unincorporated"))
city_df=puma_place_df[mask].copy()
city_df.drop('PUMA', axis=1, inplace=True)
city_df.drop('puma_to_place_factor', axis=1, inplace=True)
city_df.drop('place_code', axis=1, inplace=True)
city_df

14_VLI_hh_count  14_LI_hh_count  14_MoI_hh_count  14_HI_hh_count  \
0             2160.94          543.58          1273.46         3002.88   
1            13498.06         3395.42          7954.54        18757.12   
2             2695.44          834.79          1121.49         1532.21   
3            29015.57         8986.22         12072.51        16493.79   
4             9905.66         3217.92         10549.43        26189.31   
5              711.34          231.08           757.57         1880.69   
6            20494.00         5701.00          8693.00         4722.00   
7                0.00            0.00             0.00            0.00   
8             8204.74         3819.09          7822.15        11871.58   
10             269.01          125.22           256.46          389.23   
11            8204.74         3819.09          7822.15        11871.58   
16            1116.51          399.97           967.92         1013.43   
17              15.09            5.41            13.08           13.70   
23           14178.78         5384.70         12744.72        13192.05   
25             121.97           46.32           109.63          113.48   
27            1462.48          784.35          1986.96         3374.59   
28            2452.95         1315.55          3332.62         5660.03   
29            3814.83         2045.95          5182.91         8802.51   
31           11302.00         6548.00         15131.00        32451.00   
32            2521.49         1262.02          3536.65         9390.96   
33               0.00            0.00             0.00            0.00   
34            4853.58         2429.25          6807.64        18076.49   
35            4166.98         2085.60          5844.61        15519.33   
39              21.53           14.57            17.25           20.59   
40             365.96          247.66           293.32          350.12   
48             365.96          247.66           293.32          350.12   
82             322.90          218.52           258.81          308.93   
83             452.07          305.93           362.33          432.50   
93            1851.32         1252.85          1483.84         1771.17   
113             86.11           58.27            69.02           82.38   
...               ...             ...              ...             ...   
2055          5074.94         3292.68          2629.88         4503.47   
2057          5721.61         3712.25          2965.00         5077.33   
2067          1954.47         1219.79           782.28         1393.71   
2072          1191.75          743.77           477.00          849.82   
2073           905.73          565.27           362.52          645.87   
2080          1064.63          664.44           426.12          759.18   
2109             0.00            0.00             0.00            0.00   
2111           683.27          426.43           273.48          487.23   
2116          8085.18         6213.54          7711.64        15983.58   
2122             0.00            0.00             0.00            0.00   
2123          7812.81         5280.73          9090.27        23534.03   
2126         15175.74         9158.58          8389.42         8815.00   
2127          2702.02         1630.67          1493.73         1569.50   
2130           856.80          552.90           870.23         1200.52   
2131         10407.26         6715.89         10570.33        14582.38   
2135          1305.59          785.07           909.15         1102.53   
2138           676.53          406.81           471.11          571.31   
2140           997.00          599.51           694.26          841.93   
2141           154.30           92.78           107.45          130.30   
2143             0.00            0.00             0.00            0.00   
2144          2575.57         1548.73          1793.50         2174.99   
2145          1293.72          777.93           900.88         1092.51   
2147      

## Part 4. Regroup city and unincorporated county dfs together and drop duplicates

In [15]:
#concatenate city and county dfs together
frames = [city_df,regrouped_unin_df2]
all_df=pd.concat(frames,sort=True)
all_df

14_HI_hh_count  14_LI_hh_count  14_MoI_hh_count  14_VLI_hh_count  \
0           3002.88          543.58          1273.46          2160.94   
1          18757.12         3395.42          7954.54         13498.06   
2           1532.21          834.79          1121.49          2695.44   
3          16493.79         8986.22         12072.51         29015.57   
4          26189.31         3217.92         10549.43          9905.66   
5           1880.69          231.08           757.57           711.34   
6           4722.00         5701.00          8693.00         20494.00   
7              0.00            0.00             0.00             0.00   
8          11871.58         3819.09          7822.15          8204.74   
10           389.23          125.22           256.46           269.01   
11         11871.58         3819.09          7822.15          8204.74   
16          1013.43          399.97           967.92          1116.51   
17            13.70            5.41            13.08            15.09   
23         13192.05         5384.70         12744.72         14178.78   
25           113.48           46.32           109.63           121.97   
27          3374.59          784.35          1986.96          1462.48   
28          5660.03         1315.55          3332.62          2452.95   
29          8802.51         2045.95          5182.91          3814.83   
31         32451.00         6548.00         15131.00         11302.00   
32          9390.96         1262.02          3536.65          2521.49   
33             0.00            0.00             0.00             0.00   
34         18076.49         2429.25          6807.64          4853.58   
35         15519.33         2085.60          5844.61          4166.98   
39            20.59           14.57            17.25            21.53   
40           350.12          247.66           293.32           365.96   
48           350.12          247.66           293.32           365.96   
82           308.93          218.52           258.81           322.90   
83           432.50          305.93           362.33           452.07   
93          1771.17         1252.85          1483.84          1851.32   
113           82.38           58.27            69.02            86.11   
..              ...             ...              ...              ...   
11          3226.36         1523.14          2150.90          2888.88   
12          4410.31         2459.26          2020.70          4320.90   
13        127320.82        54978.62         16949.53         99455.52   
14          8211.01         4576.38          5257.41          6253.68   
15         12340.23         4722.67          3405.90          6646.97   
16          8460.69         4717.82          3876.50          8289.18   
17          8618.12         5278.60          5123.77          7100.80   
18         16840.94         6733.10          6920.53         10013.91   
19          4448.58         1831.28          2109.48          3008.29   
20          9762.62         4681.19          5353.16          5587.56   
21         19099.35         5191.27          5183.47          8753.09   
22         20365.63         7346.68          6332.88          9115.88   
23         61023.43        26948.29         23739.06         38820.03   
24         63205.69        40025.02         36107.24         67003.93   
25         31503.57        16242.87         16670.96         31043.71   
26         64952.90        29557.68         24108.55         39134.36   
27         15910.24         8347.86          8081.99         13336.49   
28         16522.06         6834.22          7761.06         11198.78   
29         11337.32         2976.73          2295.53          4302.13   
30         18565.87         7547.50          6206.13         13433.21   
31         12836.38         4355.54          5077.33          7071.46   
32         19204.60         9922.04          5614.18         17499.34   
33         10130.85         4486.83          4988.98          7

In [16]:
#group repeat places together
regrouped_df=all_df.groupby("Place").sum()
regrouped_df=regrouped_df.merge(ref_df,how='left',on="Place")
regrouped_df

Place  14_HI_hh_count  14_LI_hh_count  \
0            Adelanto city, CA         2030.90         1264.13   
1        Agoura Hills city, CA         5074.72          703.80   
2             Alameda city, CA        11871.58         3819.09   
3              Albany city, CA         3002.88          543.58   
4            Alhambra city, CA        11738.31         5887.68   
5         Aliso Viejo city, CA         9281.06         2233.59   
6             Alturas city, CA          392.28          149.58   
7         Amador City city, CA           20.59           14.57   
8     American Canyon city, CA         2145.56          883.23   
9             Anaheim city, CA        29783.71        21938.75   
10            Anaheim city, CA        29783.71        21938.75   
11            Anaheim city, CA        29783.71        21938.75   
12            Anaheim city, CA        29783.71        21938.75   
13            Anaheim city, CA        29783.71        21938.75   
14            Anaheim city, CA        29783.71        21938.75   
15            Anaheim city, CA        29783.71        21938.75   
16            Anaheim city, CA        29783.71        21938.75   
17            Anaheim city, CA        29783.71        21938.75   
18           Anderson city, CA         1395.58          618.08   
19             Angels city, CA          350.12          247.66   
20            Antioch city, CA         9563.33         6038.01   
21            Antioch city, CA         9563.33         6038.01   
22       Apple Valley town, CA         6618.57         4363.91   
23       Apple Valley town, CA         6618.57         4363.91   
24       Apple Valley town, CA         6618.57         4363.91   
25            Arcadia city, CA         8919.03         2732.93   
26            Arcadia city, CA         8919.03         2732.93   
27            Arcadia city, CA         8919.03         2732.93   
28             Arcata city, CA         2102.25         1171.75   
29      Arroyo Grande city, CA         2266.24         1118.07   
..                         ...             ...             ...   
828       West Covina city, CA        13378.00         7721.01   
829       West Covina city, CA        13378.00         7721.01   
830    West Hollywood city, CA        12443.76         3437.91   
831   West Sacramento city, CA         6400.30         2554.74   
832  Westlake Village city, CA         2261.56          313.65   
833       Westminster city, CA         7082.90         5744.00   
834       Westminster city, CA         7082.90         5744.00   
835       Westminster city, CA         7082.90         5744.00   
836       Westminster city, CA         7082.90         5744.00   
837       Westmorland city, CA          145.67           89.65   
838         Wheatland city, CA          442.62          229.72   
839          Whittier city, CA        13665.34         5368.53   
840          Whittier city, CA        13665.34         5368.53   
841          Wildomar city, CA         4870.25         1588.60   
842          Wildomar city, CA         4870.25         1588.60   
843          Wildomar city, CA         4870.25         1588.60   
844          Williams city, CA          439.29          248.43   
845           Willits city, CA          548.75          305.99   
846           Willows city, CA          715.88          404.84   
847           Windsor town, CA         3742.48         1233.01   
848           Winters city, CA          796.82          318.06   
849          Woodlake city, CA          487.23          426.43   
850          Woodland city, CA         6785.86         2708.64   
851          Woodside town, CA         1107.70          282.91   
852       Yorba Linda city, CA        10096.09         3505.31   
853        Yountville city, CA          452.73          186.37   
854             Yreka city, CA         1008.72          384.64   
855         Yuba City city, CA         7584.86         3936.63   
856           Yucaipa city, CA         6952.29         2137.78   

In [17]:
#drop duplicate rows
final_df = regrouped_df.drop_duplicates(subset = "Place")
final_df

Place  14_HI_hh_count  14_LI_hh_count  \
0            Adelanto city, CA         2030.90         1264.13   
1        Agoura Hills city, CA         5074.72          703.80   
2             Alameda city, CA        11871.58         3819.09   
3              Albany city, CA         3002.88          543.58   
4            Alhambra city, CA        11738.31         5887.68   
5         Aliso Viejo city, CA         9281.06         2233.59   
6             Alturas city, CA          392.28          149.58   
7         Amador City city, CA           20.59           14.57   
8     American Canyon city, CA         2145.56          883.23   
9             Anaheim city, CA        29783.71        21938.75   
18           Anderson city, CA         1395.58          618.08   
19             Angels city, CA          350.12          247.66   
20            Antioch city, CA         9563.33         6038.01   
22       Apple Valley town, CA         6618.57         4363.91   
25            Arcadia city, CA         8919.03         2732.93   
28             Arcata city, CA         2102.25         1171.75   
29      Arroyo Grande city, CA         2266.24         1118.07   
30            Artesia city, CA         2439.89          643.92   
31              Arvin city, CA         1244.62          733.82   
32         Atascadero city, CA         4721.81         1519.93   
33           Atherton town, CA         1292.32          330.06   
34            Atwater city, CA         2969.50         1615.80   
35             Auburn city, CA         2154.49          817.84   
36             Avalon city, CA         1424.72          274.65   
37             Avenal city, CA          751.90          354.97   
38              Azusa city, CA         4751.45         2485.77   
40        Bakersfield city, CA        49463.04        16709.01   
45       Baldwin Park city, CA         6337.48         3371.18   
48            Banning city, CA         3879.09         2168.45   
49            Barstow city, CA         1922.96         1261.95   
..                         ...             ...             ...   
815             Vista city, CA         9873.97         5212.63   
819      Walnut Creek city, CA        17049.86         3209.05   
821            Walnut city, CA         4306.57         1907.87   
822             Wasco city, CA         2020.47         1008.38   
823         Waterford city, CA         1020.60          445.61   
824       Watsonville city, CA         4636.25         2778.22   
826              Weed city, CA          354.92          135.34   
827       West Covina city, CA        13378.00         7721.01   
830    West Hollywood city, CA        12443.76         3437.91   
831   West Sacramento city, CA         6400.30         2554.74   
832  Westlake Village city, CA         2261.56          313.65   
833       Westminster city, CA         7082.90         5744.00   
837       Westmorland city, CA          145.67           89.65   
838         Wheatland city, CA          442.62          229.72   
839          Whittier city, CA        13665.34         5368.53   
841          Wildomar city, CA         4870.25         1588.60   
844          Williams city, CA          439.29          248.43   
845           Willits city, CA          548.75          305.99   
846           Willows city, CA          715.88          404.84   
847           Windsor town, CA         3742.48         1233.01   
848           Winters city, CA          796.82          318.06   
849          Woodlake city, CA          487.23          426.43   
850          Woodland city, CA         6785.86         2708.64   
851          Woodside town, CA         1107.70          282.91   
852       Yorba Linda city, CA        10096.09         3505.31   
853        Yountville city, CA          452.73          186.37   
854             Yreka city, CA         1008.72          384.64   
855         Yuba City city, CA         7584.86         3936.63   
856           Yucaipa city, CA         6952.29         2137.78   

In [18]:
# add county names to "County" column for unincorporated county areas
mask = final_df["County"].isna()
column_name = "County"
fill = final_df["Place"]
final_df.loc[mask, column_name]=fill
final_df['County'] = final_df['County'].str.replace(r'Unincorporated_', '')
final_df

C:\Users\jonst\Anaconda3\lib\site-packages\pandas\core\indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s
C:\Users\jonst\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


Place  14_HI_hh_count  14_LI_hh_count  \
0            Adelanto city, CA         2030.90         1264.13   
1        Agoura Hills city, CA         5074.72          703.80   
2             Alameda city, CA        11871.58         3819.09   
3              Albany city, CA         3002.88          543.58   
4            Alhambra city, CA        11738.31         5887.68   
5         Aliso Viejo city, CA         9281.06         2233.59   
6             Alturas city, CA          392.28          149.58   
7         Amador City city, CA           20.59           14.57   
8     American Canyon city, CA         2145.56          883.23   
9             Anaheim city, CA        29783.71        21938.75   
18           Anderson city, CA         1395.58          618.08   
19             Angels city, CA          350.12          247.66   
20            Antioch city, CA         9563.33         6038.01   
22       Apple Valley town, CA         6618.57         4363.91   
25            Arcadia city, CA         8919.03         2732.93   
28             Arcata city, CA         2102.25         1171.75   
29      Arroyo Grande city, CA         2266.24         1118.07   
30            Artesia city, CA         2439.89          643.92   
31              Arvin city, CA         1244.62          733.82   
32         Atascadero city, CA         4721.81         1519.93   
33           Atherton town, CA         1292.32          330.06   
34            Atwater city, CA         2969.50         1615.80   
35             Auburn city, CA         2154.49          817.84   
36             Avalon city, CA         1424.72          274.65   
37             Avenal city, CA          751.90          354.97   
38              Azusa city, CA         4751.45         2485.77   
40        Bakersfield city, CA        49463.04        16709.01   
45       Baldwin Park city, CA         6337.48         3371.18   
48            Banning city, CA         3879.09         2168.45   
49            Barstow city, CA         1922.96         1261.95   
..                         ...             ...             ...   
815             Vista city, CA         9873.97         5212.63   
819      Walnut Creek city, CA        17049.86         3209.05   
821            Walnut city, CA         4306.57         1907.87   
822             Wasco city, CA         2020.47         1008.38   
823         Waterford city, CA         1020.60          445.61   
824       Watsonville city, CA         4636.25         2778.22   
826              Weed city, CA          354.92          135.34   
827       West Covina city, CA        13378.00         7721.01   
830    West Hollywood city, CA        12443.76         3437.91   
831   West Sacramento city, CA         6400.30         2554.74   
832  Westlake Village city, CA         2261.56          313.65   
833       Westminster city, CA         7082.90         5744.00   
837       Westmorland city, CA          145.67           89.65   
838         Wheatland city, CA          442.62          229.72   
839          Whittier city, CA        13665.34         5368.53   
841          Wildomar city, CA         4870.25         1588.60   
844          Williams city, CA          439.29          248.43   
845           Willits city, CA          548.75          305.99   
846           Willows city, CA          715.88          404.84   
847           Windsor town, CA         3742.48         1233.01   
848           Winters city, CA          796.82          318.06   
849          Woodlake city, CA          487.23          426.43   
850          Woodland city, CA         6785.86         2708.64   
851          Woodside town, CA         1107.70          282.91   
852       Yorba Linda city, CA        10096.09         3505.31   
853        Yountville city, CA          452.73          186.37   
854             Yreka city, CA         1008.72          384.64   
855         Yuba City city, CA         7584.86         3936.63   
856           Yucaipa city, CA         6952.29         2137.78   

In [19]:
# Reassign cities from Lake to Mendocino County
mask = (final_df.Place=="Fort Bragg city, CA")|(final_df.Place=="Point Arena city, CA")|(final_df.Place=="Ukiah city, CA")|(final_df.Place=="Willits city, CA")
column_name = "County"
fill = "Mendocino"
final_df.loc[mask, column_name]=fill

In [20]:
#drop rows outside study area
bay_mask = ((final_df["County"]=="San Francisco")|
    (final_df["County"]=="Alameda")|
    (final_df["County"]=="Contra Costa")|
    (final_df["County"]=="Marin")|
    (final_df["County"]=="San Mateo")|
    (final_df["County"]=="Santa Clara")|
    (final_df["County"]=="Napa")|
    (final_df["County"]=="Sonoma")|
    (final_df["County"]=="Solano")|
    (final_df["County"]=="Napa")|
    (final_df["County"]=="Sacramento")|
    (final_df["County"]=="San Joaquin")|
    (final_df["County"]=="Stanislaus")|
    (final_df["County"]=="Santa Cruz")|
    (final_df["County"]=="Monterey")|
    (final_df["County"]=="Placer")|
    (final_df["County"]=="Yolo")|
    (final_df["County"]=="Fresno")|
    (final_df["County"]=="Merced")|
    (final_df["County"]=="El Dorado")|
    (final_df["County"]=="San Benito")|
    (final_df["County"]=="Mendocino"))
bas_df = final_df[bay_mask].copy()
bas_df

Place  14_HI_hh_count  14_LI_hh_count  \
2              Alameda city, CA        11871.58         3819.09   
3               Albany city, CA         3002.88          543.58   
8      American Canyon city, CA         2145.56          883.23   
20             Antioch city, CA         9563.33         6038.01   
33            Atherton town, CA         1292.32          330.06   
34             Atwater city, CA         2969.50         1615.80   
35              Auburn city, CA         2154.49          817.84   
55             Belmont city, CA         5225.26         1451.52   
56           Belvedere city, CA          501.17          157.55   
57             Benicia city, CA         3662.20         1545.60   
58            Berkeley city, CA        18757.12         3395.42   
69           Brentwood city, CA         6308.82         2287.07   
71            Brisbane city, CA          661.25          332.44   
77          Burlingame city, CA         6260.59         1887.39   
83           Calistoga city, CA          826.73          340.33   
85            Campbell city, CA         6821.61         2779.87   
92            Capitola city, CA         1928.06          815.26   
95   Carmel-by-the-Sea city, CA         1360.73          434.42   
102              Ceres city, CA         4080.41         2589.29   
114     Citrus Heights city, CA         9427.22         8179.57   
117            Clayton city, CA         1973.42          414.38   
119         Cloverdale city, CA         1336.60          440.36   
120             Clovis city, CA        18830.84         4022.22   
124           Coalinga city, CA         1077.06          869.80   
125             Colfax city, CA          328.30          124.62   
126              Colma town, CA          183.53           97.88   
134            Concord city, CA        17386.68         6218.00   
143       Corte Madera town, CA         1942.03          610.51   
147             Cotati city, CA         1195.33          490.97   
154          Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
765    Unincorporated_El Dorado        22896.66         7282.76   
766       Unincorporated_Fresno        18453.65         9815.83   
774        Unincorporated_Marin        12340.23         4722.67   
775    Unincorporated_Mendocino         8460.69         4717.82   
776       Unincorporated_Merced         8618.12         5278.60   
777     Unincorporated_Monterey        16840.94         6733.10   
778         Unincorporated_Napa         4448.58         1831.28   
781       Unincorporated_Placer        20365.63         7346.68   
783   Unincorporated_Sacramento        63205.69        40025.02   
786  Unincorporated_San Joaquin        15910.24         8347.86   
788    Unincorporated_San Mateo        11337.32         2976.73   
790  Unincorporated_Santa Clara        12836.38         4355.54   
791   Unincorporated_Santa Cruz        19204.60         9922.04   
793       Unincorporated_Solano         2632.31         1156.47   
794       Unincorporated_Sonoma        25859.39         9488.09   
795   Unincorporated_Stanislaus        12590.34         6427.55   
799         Unincorporated_Yolo         2878.85         1149.12   
800         Union City city, CA         8915.99         2092.27   
803          Vacaville city, CA        11643.79         4932.77   
805            Vallejo city, CA        14421.87         6098.56   
819       Walnut Creek city, CA        17049.86         3209.05   
823          Waterford city, CA         1020.60          445.61   
824        Watsonville city, CA         4636.25         2778.22   
831    West Sacramento city, CA         6400.30         2554.74   
845            Willits city, CA          548.75          305.99   
847            Windsor town, CA         3742.48         1233.01   
848            Winters city, CA          796.82          318.06   
850           Woodland city, CA         6785.86         2708.64   
851   

In [21]:
#export it
bas_df.to_csv("hh_by_city_and_county.csv")

## Part B1. Copy BAS scenario df and import RHNA allocations by city and county

In [22]:
#copy BAS df
needs_df = bas_df.copy()
needs_df

Place  14_HI_hh_count  14_LI_hh_count  \
2              Alameda city, CA        11871.58         3819.09   
3               Albany city, CA         3002.88          543.58   
8      American Canyon city, CA         2145.56          883.23   
20             Antioch city, CA         9563.33         6038.01   
33            Atherton town, CA         1292.32          330.06   
34             Atwater city, CA         2969.50         1615.80   
35              Auburn city, CA         2154.49          817.84   
55             Belmont city, CA         5225.26         1451.52   
56           Belvedere city, CA          501.17          157.55   
57             Benicia city, CA         3662.20         1545.60   
58            Berkeley city, CA        18757.12         3395.42   
69           Brentwood city, CA         6308.82         2287.07   
71            Brisbane city, CA          661.25          332.44   
77          Burlingame city, CA         6260.59         1887.39   
83           Calistoga city, CA          826.73          340.33   
85            Campbell city, CA         6821.61         2779.87   
92            Capitola city, CA         1928.06          815.26   
95   Carmel-by-the-Sea city, CA         1360.73          434.42   
102              Ceres city, CA         4080.41         2589.29   
114     Citrus Heights city, CA         9427.22         8179.57   
117            Clayton city, CA         1973.42          414.38   
119         Cloverdale city, CA         1336.60          440.36   
120             Clovis city, CA        18830.84         4022.22   
124           Coalinga city, CA         1077.06          869.80   
125             Colfax city, CA          328.30          124.62   
126              Colma town, CA          183.53           97.88   
134            Concord city, CA        17386.68         6218.00   
143       Corte Madera town, CA         1942.03          610.51   
147             Cotati city, CA         1195.33          490.97   
154          Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
765    Unincorporated_El Dorado        22896.66         7282.76   
766       Unincorporated_Fresno        18453.65         9815.83   
774        Unincorporated_Marin        12340.23         4722.67   
775    Unincorporated_Mendocino         8460.69         4717.82   
776       Unincorporated_Merced         8618.12         5278.60   
777     Unincorporated_Monterey        16840.94         6733.10   
778         Unincorporated_Napa         4448.58         1831.28   
781       Unincorporated_Placer        20365.63         7346.68   
783   Unincorporated_Sacramento        63205.69        40025.02   
786  Unincorporated_San Joaquin        15910.24         8347.86   
788    Unincorporated_San Mateo        11337.32         2976.73   
790  Unincorporated_Santa Clara        12836.38         4355.54   
791   Unincorporated_Santa Cruz        19204.60         9922.04   
793       Unincorporated_Solano         2632.31         1156.47   
794       Unincorporated_Sonoma        25859.39         9488.09   
795   Unincorporated_Stanislaus        12590.34         6427.55   
799         Unincorporated_Yolo         2878.85         1149.12   
800         Union City city, CA         8915.99         2092.27   
803          Vacaville city, CA        11643.79         4932.77   
805            Vallejo city, CA        14421.87         6098.56   
819       Walnut Creek city, CA        17049.86         3209.05   
823          Waterford city, CA         1020.60          445.61   
824        Watsonville city, CA         4636.25         2778.22   
831    West Sacramento city, CA         6400.30         2554.74   
845            Willits city, CA          548.75          305.99   
847            Windsor town, CA         3742.48         1233.01   
848            Winters city, CA          796.82          318.06   
850           Woodland city, CA         6785.86         2708.64   
851   

In [23]:
#Bring in RHNA allocation numbers
col = ["Place","Very Low","Low","Mod","Above Mod"]
rnha_df = pd.read_csv("rhna_allocations.csv", delimiter=",",usecols=col)
rnha_df

Place  Very Low   Low   Mod  Above Mod
0              Alameda city, CA       444   248   283        748
1               Albany city, CA        80    53    57        145
2             Berkeley city, CA       532   442   584       1401
3               Dublin city, CA       796   446   425        618
4           Emeryville city, CA       276   211   259        752
5              Fremont city, CA      1714   926   978       1837
6              Hayward city, CA       851   480   608       1981
7            Livermore city, CA       839   474   496        920
8               Newark city, CA       330   167   158        423
9              Oakland city, CA      2059  2075  2815       7816
10            Piedmont city, CA        24    14    15          7
11          Pleasanton city, CA       716   391   407        553
12         San Leandro city, CA       504   270   352       1161
13          Union City city, CA       317   180   192        417
14       Unincorporated_Alameda       430   227   295        817
15             Antioch city, CA       349   205   214        680
16           Brentwood city, CA       234   124   123        279
17             Clayton city, CA        51    25    31         34
18             Concord city, CA       798   444   559       1677
19            Danville town, CA       196   111   124        126
20          El Cerrito city, CA       100    63    69        166
21            Hercules city, CA       220   118   100        244
22           Lafayette city, CA       138    78    85         99
23            Martinez city, CA       124    72    78        195
24              Moraga city, CA        75    44    50         60
25              Oakley city, CA       317   174   175        502
26              Orinda city, CA        84    47    54         42
27              Pinole city, CA        80    48    43        126
28           Pittsburg city, CA       392   254   316       1063
29       Pleasant Hill city, CA       118    69    84        177
..                          ...       ...   ...   ...        ...
79     Los Altos Hills town, CA        46    28    32         15
80           Los Gatos town, CA       201   112   132        174
81            Milpitas city, CA      1004   570   565       1151
82        Monte Sereno city, CA        23    13    13         12
83         Morgan Hill city, CA       273   154   185        316
84       Mountain View city, CA       814   492   527       1093
85           Palo Alto city, CA       691   432   278        587
86            San Jose city, CA      9233  5428  6188      14231
87         Santa Clara city, CA      1050   695   755       1593
88            Saratoga city, CA       147    95   104         93
89           Sunnyvale city, CA      1640   906   932       1974
90   Unincorporated_Santa Clara        22    13   214         28
91             Benicia city, CA        94    54    56        123
92               Dixon city, CA        50    24    30         93
93           Fairfield city, CA       779   404   456       1461
94           Rio Vista city, CA        45    36    48        170
95         Suisun City city, CA       147    57    60        241
96           Vacaville city, CA       287   134   173        490
97             Vallejo city, CA       283   178   211        690
98        Unincorporated_Solano        26    15    19         43
99          Cloverdale city, CA        39    29    31        112
100             Cotati city, CA        35    18    18         66
101         Healdsburg city, CA        31    24    26         76
102           Petaluma city, CA       199   103   121        322
103       Rohnert Park city, CA       181   107   127        484
104         Santa Rosa city, CA      1041   671   759       2612
105         Sebastopol city, CA        22    17    19         62
106             Sonoma city, CA        24    23    27         63
107            Windsor town, CA       120    65    67        188
108       Unincorporated_Sonoma       126    37   160        

In [24]:
# divide variables by 8 to get yearly amounts
rnha_df["Very Low"]=rnha_df["Very Low"]*0.125
rnha_df["Low"]=rnha_df["Low"]*0.125
rnha_df["Mod"]=rnha_df["Mod"]*0.125
rnha_df["Above Mod"]=rnha_df["Above Mod"]*0.125
rnha_df

Place  Very Low    Low    Mod  Above Mod
0              Alameda city, CA     55.50  31.00  35.38      93.50
1               Albany city, CA     10.00   6.62   7.12      18.12
2             Berkeley city, CA     66.50  55.25  73.00     175.12
3               Dublin city, CA     99.50  55.75  53.12      77.25
4           Emeryville city, CA     34.50  26.38  32.38      94.00
5              Fremont city, CA    214.25 115.75 122.25     229.62
6              Hayward city, CA    106.38  60.00  76.00     247.62
7            Livermore city, CA    104.88  59.25  62.00     115.00
8               Newark city, CA     41.25  20.88  19.75      52.88
9              Oakland city, CA    257.38 259.38 351.88     977.00
10            Piedmont city, CA      3.00   1.75   1.88       0.88
11          Pleasanton city, CA     89.50  48.88  50.88      69.12
12         San Leandro city, CA     63.00  33.75  44.00     145.12
13          Union City city, CA     39.62  22.50  24.00      52.12
14       Unincorporated_Alameda     53.75  28.38  36.88     102.12
15             Antioch city, CA     43.62  25.62  26.75      85.00
16           Brentwood city, CA     29.25  15.50  15.38      34.88
17             Clayton city, CA      6.38   3.12   3.88       4.25
18             Concord city, CA     99.75  55.50  69.88     209.62
19            Danville town, CA     24.50  13.88  15.50      15.75
20          El Cerrito city, CA     12.50   7.88   8.62      20.75
21            Hercules city, CA     27.50  14.75  12.50      30.50
22           Lafayette city, CA     17.25   9.75  10.62      12.38
23            Martinez city, CA     15.50   9.00   9.75      24.38
24              Moraga city, CA      9.38   5.50   6.25       7.50
25              Oakley city, CA     39.62  21.75  21.88      62.75
26              Orinda city, CA     10.50   5.88   6.75       5.25
27              Pinole city, CA     10.00   6.00   5.38      15.75
28           Pittsburg city, CA     49.00  31.75  39.50     132.88
29       Pleasant Hill city, CA     14.75   8.62  10.50      22.12
..                          ...       ...    ...    ...        ...
79     Los Altos Hills town, CA      5.75   3.50   4.00       1.88
80           Los Gatos town, CA     25.12  14.00  16.50      21.75
81            Milpitas city, CA    125.50  71.25  70.62     143.88
82        Monte Sereno city, CA      2.88   1.62   1.62       1.50
83         Morgan Hill city, CA     34.12  19.25  23.12      39.50
84       Mountain View city, CA    101.75  61.50  65.88     136.62
85           Palo Alto city, CA     86.38  54.00  34.75      73.38
86            San Jose city, CA   1154.12 678.50 773.50    1778.88
87         Santa Clara city, CA    131.25  86.88  94.38     199.12
88            Saratoga city, CA     18.38  11.88  13.00      11.62
89           Sunnyvale city, CA    205.00 113.25 116.50     246.75
90   Unincorporated_Santa Clara      2.75   1.62  26.75       3.50
91             Benicia city, CA     11.75   6.75   7.00      15.38
92               Dixon city, CA      6.25   3.00   3.75      11.62
93           Fairfield city, CA     97.38  50.50  57.00     182.62
94           Rio Vista city, CA      5.62   4.50   6.00      21.25
95         Suisun City city, CA     18.38   7.12   7.50      30.12
96           Vacaville city, CA     35.88  16.75  21.62      61.25
97             Vallejo city, CA     35.38  22.25  26.38      86.25
98        Unincorporated_Solano      3.25   1.88   2.38       5.38
99          Cloverdale city, CA      4.88   3.62   3.88      14.00
100             Cotati city, CA      4.38   2.25   2.25       8.25
101         Healdsburg city, CA      3.88   3.00   3.25       9.50
102           Petaluma city, CA     24.88  12.88  15.12      40.25
103       Rohnert Park city, CA     22.62  13.38  15.88      60.50
104         Santa Rosa city, CA    130.12  83.88  94.88     326.50
105         Sebastopol city, CA      2.75   2.12   2.38       7.75
106             Sonoma city, CA      3.00   2.88   3.38       7.88
107   

In [25]:
needs_df = needs_df.merge(rnha_df,on = "Place",how="left")
needs_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.60          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

## Part B2. Calculate difference between RHNA allocations and changes in household counts over time period

In [26]:
#calculate number of households if each jurisdiction in ABAG had met 1/8 of RHNA goals each year
needs_df["15_VLI_hh_needs"]=needs_df["14_VLI_hh_count"]+needs_df["Very Low"]
needs_df["15_LI_hh_needs"]=needs_df["14_LI_hh_count"]+needs_df["Low"]
needs_df["15_MoI_hh_needs"]=needs_df["14_MoI_hh_count"]+needs_df["Mod"]
needs_df["15_HI_hh_needs"]=needs_df["14_HI_hh_count"]+needs_df["Above Mod"]

needs_df["16_VLI_hh_needs"]=needs_df["14_VLI_hh_count"]+(2*needs_df["Very Low"])
needs_df["16_LI_hh_needs"]=needs_df["14_LI_hh_count"]+(2*needs_df["Low"])
needs_df["16_MoI_hh_needs"]=needs_df["14_MoI_hh_count"]+(2*needs_df["Mod"])
needs_df["16_HI_hh_needs"]=needs_df["14_HI_hh_count"]+(2*needs_df["Above Mod"])

needs_df["17_VLI_hh_needs"]=needs_df["14_VLI_hh_count"]+(3*needs_df["Very Low"])
needs_df["17_LI_hh_needs"]=needs_df["14_LI_hh_count"]+(3*needs_df["Low"])
needs_df["17_MoI_hh_needs"]=needs_df["14_MoI_hh_count"]+(3*needs_df["Mod"])
needs_df["17_HI_hh_needs"]=needs_df["14_HI_hh_count"]+(3*needs_df["Above Mod"])

needs_df["18_VLI_hh_needs"]=needs_df["14_VLI_hh_count"]+(4*needs_df["Very Low"])
needs_df["18_LI_hh_needs"]=needs_df["14_LI_hh_count"]+(4*needs_df["Low"])
needs_df["18_MoI_hh_needs"]=needs_df["14_MoI_hh_count"]+(4*needs_df["Mod"])
needs_df["18_HI_hh_needs"]=needs_df["14_HI_hh_count"]+(4*needs_df["Above Mod"])
needs_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.60          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [27]:
#determine which is larger and use that for new "mod" variable
needs_df["15_VLI_hh_mod"]= needs_df[['15_VLI_hh_count', '15_VLI_hh_needs']].values.max(1)
needs_df["16_VLI_hh_mod"]= needs_df[['16_VLI_hh_count', '16_VLI_hh_needs']].values.max(1)
needs_df["17_VLI_hh_mod"]= needs_df[['17_VLI_hh_count', '17_VLI_hh_needs']].values.max(1)
needs_df["18_VLI_hh_mod"]= needs_df[['18_VLI_hh_count', '18_VLI_hh_needs']].values.max(1)

needs_df["15_LI_hh_mod"]= needs_df[['15_LI_hh_count', '15_LI_hh_needs']].values.max(1)
needs_df["16_LI_hh_mod"]= needs_df[['16_LI_hh_count', '16_LI_hh_needs']].values.max(1)
needs_df["17_LI_hh_mod"]= needs_df[['17_LI_hh_count', '17_LI_hh_needs']].values.max(1)
needs_df["18_LI_hh_mod"]= needs_df[['18_LI_hh_count', '18_LI_hh_needs']].values.max(1)

needs_df["15_MoI_hh_mod"]= needs_df[['15_MoI_hh_count', '15_MoI_hh_needs']].values.max(1)
needs_df["16_MoI_hh_mod"]= needs_df[['16_MoI_hh_count', '16_MoI_hh_needs']].values.max(1)
needs_df["17_MoI_hh_mod"]= needs_df[['17_MoI_hh_count', '17_MoI_hh_needs']].values.max(1)
needs_df["18_MoI_hh_mod"]= needs_df[['18_MoI_hh_count', '18_MoI_hh_needs']].values.max(1)

needs_df["15_HI_hh_mod"]= needs_df[['15_HI_hh_count', '15_HI_hh_needs']].values.max(1)
needs_df["16_HI_hh_mod"]= needs_df[['16_HI_hh_count', '16_HI_hh_needs']].values.max(1)
needs_df["17_HI_hh_mod"]= needs_df[['17_HI_hh_count', '17_HI_hh_needs']].values.max(1)
needs_df["18_HI_hh_mod"]= needs_df[['18_HI_hh_count', '18_HI_hh_needs']].values.max(1)

needs_df[["17_MoI_hh_mod","17_MoI_hh_count","17_MoI_hh_needs","County"]]

17_MoI_hh_mod  17_MoI_hh_count  17_MoI_hh_needs        County
0          7928.28          5168.90          7928.28       Alameda
1          1294.84           968.21          1294.84       Alameda
2          1039.53          1039.53          1039.16          Napa
3          7724.18          6735.41          7724.18  Contra Costa
4           207.81           201.79           207.81     San Mateo
5              nan          1530.10              nan        Merced
6              nan           918.33              nan        Placer
7          1169.06           931.18          1169.06     San Mateo
8           104.80           104.80           101.69         Marin
9          2329.40          2329.40          2230.60        Solano
10         8173.54          6047.79          8173.54       Alameda
11         4792.43          3092.07          4792.43  Contra Costa
12          308.31           296.42           308.31     San Mateo
13         1748.92          1748.92          1730.08     San Mateo
14          400.55           400.55           393.53          Napa
15         3504.45          3424.97          3504.45   Santa Clara
16             nan           487.24              nan    Santa Cruz
17             nan           309.35              nan      Monterey
18             nan          2220.66              nan    Stanislaus
19             nan          7938.25              nan    Sacramento
20          968.89           832.07           968.89  Contra Costa
21          596.90           454.84           596.90        Sonoma
22             nan          5210.05              nan        Fresno
23             nan           852.04              nan        Fresno
24             nan           139.94              nan        Placer
25           99.93            86.17            99.93     San Mateo
26        11282.30          8956.03         11282.30  Contra Costa
27          406.10           406.10           393.12         Marin
28          639.10           541.40           639.10        Sonoma
29         3490.06          3490.06          3357.42   Santa Clara
..             ...              ...              ...           ...
168            nan          9668.96              nan     El Dorado
169            nan          9934.98              nan        Fresno
170        3419.77          3060.46          3419.77         Marin
171            nan          3846.94              nan     Mendocino
172            nan          5193.65              nan        Merced
173            nan          4951.91              nan      Monterey
174        2155.36          2155.36          2121.48          Napa
175            nan          8471.13              nan        Placer
176            nan         37366.78              nan    Sacramento
177            nan          7857.75              nan   San Joaquin
178        2333.78          2139.07          2333.78     San Mateo
179        5696.20          5696.20          5157.58   Santa Clara
180            nan          5388.83              nan    Santa Cruz
181        1578.34          1328.59          1578.34        Solano
182       11840.67          9766.46         11840.67        Sonoma
183            nan          6106.91              nan    Stanislaus
184            nan          1228.64              nan          Yolo
185        5364.54          3730.21          5364.54       Alameda
186        6996.26          5232.15          6996.26        Solano
187        9160.01          9160.01          8779.46        Solano
188        7064.88          5085.32          7064.88  Contra Costa
189            nan           421.36              nan    Stanislaus
190            nan          1414.78              nan    Santa Cruz
191            nan          2731.53              nan          Yolo
192            nan           249.51              nan     Mendocino
193        1663.91          1273.55          1663.91        Sonoma
194            nan           340.07              nan          Yolo
195            nan          2896.08              nan

In [145]:
# add back in values from outside bay area for model numbers
needs_df["15_VLI_hh_mod"]= np.where(needs_df["15_VLI_hh_mod"].isna(),needs_df["15_VLI_hh_count"],needs_df["15_VLI_hh_mod"])
needs_df["16_VLI_hh_mod"]= np.where(needs_df["16_VLI_hh_mod"].isna(),needs_df["16_VLI_hh_count"],needs_df["16_VLI_hh_mod"])
needs_df["17_VLI_hh_mod"]= np.where(needs_df["17_VLI_hh_mod"].isna(),needs_df["17_VLI_hh_count"],needs_df["17_VLI_hh_mod"])
needs_df["18_VLI_hh_mod"]= np.where(needs_df["18_VLI_hh_mod"].isna(),needs_df["18_VLI_hh_count"],needs_df["18_VLI_hh_mod"])

needs_df["15_LI_hh_mod"]= np.where(needs_df["15_LI_hh_mod"].isna(),needs_df["15_LI_hh_count"],needs_df["15_LI_hh_mod"])
needs_df["16_LI_hh_mod"]= np.where(needs_df["16_LI_hh_mod"].isna(),needs_df["16_LI_hh_count"],needs_df["16_LI_hh_mod"])
needs_df["17_LI_hh_mod"]= np.where(needs_df["17_LI_hh_mod"].isna(),needs_df["17_LI_hh_count"],needs_df["17_LI_hh_mod"])
needs_df["18_LI_hh_mod"]= np.where(needs_df["18_LI_hh_mod"].isna(),needs_df["18_LI_hh_count"],needs_df["18_LI_hh_mod"])

needs_df["15_MoI_hh_mod"]= np.where(needs_df["15_MoI_hh_mod"].isna(),needs_df["15_MoI_hh_count"],needs_df["15_MoI_hh_mod"])
needs_df["16_MoI_hh_mod"]= np.where(needs_df["16_MoI_hh_mod"].isna(),needs_df["16_MoI_hh_count"],needs_df["16_MoI_hh_mod"])
needs_df["17_MoI_hh_mod"]= np.where(needs_df["17_MoI_hh_mod"].isna(),needs_df["17_MoI_hh_count"],needs_df["17_MoI_hh_mod"])
needs_df["18_MoI_hh_mod"]= np.where(needs_df["18_MoI_hh_mod"].isna(),needs_df["18_MoI_hh_count"],needs_df["18_MoI_hh_mod"])

needs_df["15_HI_hh_mod"]= np.where(needs_df["15_HI_hh_mod"].isna(),needs_df["15_HI_hh_count"],needs_df["15_HI_hh_mod"])
needs_df["16_HI_hh_mod"]= np.where(needs_df["16_HI_hh_mod"].isna(),needs_df["16_HI_hh_count"],needs_df["16_HI_hh_mod"])
needs_df["17_HI_hh_mod"]= np.where(needs_df["17_HI_hh_mod"].isna(),needs_df["17_HI_hh_count"],needs_df["17_HI_hh_mod"])
needs_df["18_HI_hh_mod"]= np.where(needs_df["18_HI_hh_mod"].isna(),needs_df["18_HI_hh_count"],needs_df["18_HI_hh_mod"])

needs_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.60          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [146]:
#calculate difference between "mod" and "count"
needs_df["15_VLI_hh_dif"]=needs_df["15_VLI_hh_needs"]-needs_df["15_VLI_hh_count"]
needs_df["16_VLI_hh_dif"]=needs_df["16_VLI_hh_needs"]-needs_df["16_VLI_hh_count"]
needs_df["17_VLI_hh_dif"]=needs_df["17_VLI_hh_needs"]-needs_df["17_VLI_hh_count"]
needs_df["18_VLI_hh_dif"]=needs_df["18_VLI_hh_needs"]-needs_df["18_VLI_hh_count"]

needs_df["15_LI_hh_dif"]=needs_df["15_LI_hh_needs"]-needs_df["15_LI_hh_count"]
needs_df["16_LI_hh_dif"]=needs_df["16_LI_hh_needs"]-needs_df["16_LI_hh_count"]
needs_df["17_LI_hh_dif"]=needs_df["17_LI_hh_needs"]-needs_df["17_LI_hh_count"]
needs_df["18_LI_hh_dif"]=needs_df["18_LI_hh_needs"]-needs_df["18_LI_hh_count"]

needs_df["15_MoI_hh_dif"]=needs_df["15_MoI_hh_needs"]-needs_df["15_MoI_hh_count"]
needs_df["16_MoI_hh_dif"]=needs_df["16_MoI_hh_needs"]-needs_df["16_MoI_hh_count"]
needs_df["17_MoI_hh_dif"]=needs_df["17_MoI_hh_needs"]-needs_df["17_MoI_hh_count"]
needs_df["18_MoI_hh_dif"]=needs_df["18_MoI_hh_needs"]-needs_df["18_MoI_hh_count"]

needs_df["15_HI_hh_dif"]=needs_df["15_HI_hh_needs"]-needs_df["15_HI_hh_count"]
needs_df["16_HI_hh_dif"]=needs_df["16_HI_hh_needs"]-needs_df["16_HI_hh_count"]
needs_df["17_HI_hh_dif"]=needs_df["17_HI_hh_needs"]-needs_df["17_HI_hh_count"]
needs_df["18_HI_hh_dif"]=needs_df["18_HI_hh_needs"]-needs_df["18_HI_hh_count"]

needs_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.60          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [147]:
#export it
needs_df.to_csv("diff.csv")

In [148]:
needs_df[needs_df["18_HI_hh_dif"]<0]

Place  14_HI_hh_count  14_LI_hh_count  \
0                Alameda city, CA        11871.58         3819.09   
1                 Albany city, CA         3002.88          543.58   
2        American Canyon city, CA         2145.56          883.23   
3                Antioch city, CA         9563.33         6038.01   
7                Belmont city, CA         5225.26         1451.52   
8              Belvedere city, CA          501.17          157.55   
9                Benicia city, CA         3662.20         1545.60   
11             Brentwood city, CA         6308.82         2287.07   
12              Brisbane city, CA          661.25          332.44   
13            Burlingame city, CA         6260.59         1887.39   
14             Calistoga city, CA          826.73          340.33   
15              Campbell city, CA         6821.61         2779.87   
20               Clayton city, CA         1973.42          414.38   
21            Cloverdale city, CA         1336.60          440.36   
26               Concord city, CA        17386.68         6218.00   
27          Corte Madera town, CA         1942.03          610.51   
28                Cotati city, CA         1195.33          490.97   
29             Cupertino city, CA        11457.08         2689.71   
30             Daly City city, CA        10620.99         5638.72   
31              Danville town, CA         9989.33         1165.50   
34                 Dixon city, CA         2184.26          925.34   
36                Dublin city, CA         9390.96         1262.02   
40            Emeryville city, CA         1532.21          834.79   
42               Fairfax town, CA         1416.82          584.61   
43             Fairfield city, CA        13386.75         6558.30   
49               Fremont city, CA        35825.60         7332.35   
52                Gilroy city, CA         6589.02         2109.54   
57               Hayward city, CA        14205.48         5784.67   
58            Healdsburg city, CA         1871.24          616.50   
60          Hillsborough town, CA         1880.24          566.84   
..                            ...             ...             ...   
133           San Carlos city, CA         5684.88         1579.20   
134        San Francisco city, CA       150124.00        49404.00   
136             San Jose city, CA       113236.43        56270.04   
138          San Leandro city, CA        11885.27         3824.49   
140            San Pablo city, CA         1450.61         1380.69   
141           San Rafael city, CA        10531.40         3787.27   
142            San Ramon city, CA        16628.78         1859.19   
145          Santa Clara city, CA        18926.57         6737.50   
147           Santa Rosa city, CA        22091.29        12286.03   
148             Saratoga city, CA         6034.50         1440.11   
149            Sausalito city, CA         2192.61          689.29   
152           Sebastopol city, CA         1370.01          451.37   
155               Sonoma city, CA         2171.97          715.59   
157  South San Francisco city, CA         7532.50         3786.95   
158           St. Helena city, CA         1003.88          413.25   
160          Suisun City city, CA         3395.06         1663.27   
161            Sunnyvale city, CA        26702.28         5596.47   
162              Tiburon town, CA         1942.03          610.51   
166        Unincorporated_Alameda        14844.19         5569.34   
167   Unincorporated_Contra Costa        25402.32         7390.29   
170          Unincorporated_Marin        12340.23         4722.67   
174           Unincorporated_Napa         4448.58         1831.28   
179    Unincorporated_Santa Clara        12836.38         4355.54   
181         Unincorporated_Solano         2632.31         1156.47   
182         Unincorporated_Sonoma        25859.39         9488.09   
185           Union City city, CA         8915.99         2092.27   
186            Vacaville c

In [149]:
needs_df["15_VLI_hh_ex"]=np.where(needs_df["15_VLI_hh_dif"]>0,needs_df["15_VLI_hh_dif"],0)
needs_df["16_VLI_hh_ex"]=np.where(needs_df["16_VLI_hh_dif"]>0,needs_df["16_VLI_hh_dif"],0)
needs_df["17_VLI_hh_ex"]=np.where(needs_df["17_VLI_hh_dif"]>0,needs_df["17_VLI_hh_dif"],0)
needs_df["18_VLI_hh_ex"]=np.where(needs_df["18_VLI_hh_dif"]>0,needs_df["18_VLI_hh_dif"],0)

needs_df["15_LI_hh_ex"]=np.where(needs_df["15_LI_hh_dif"]>0,needs_df["15_LI_hh_dif"],0)
needs_df["16_LI_hh_ex"]=np.where(needs_df["16_LI_hh_dif"]>0,needs_df["16_LI_hh_dif"],0)
needs_df["17_LI_hh_ex"]=np.where(needs_df["17_LI_hh_dif"]>0,needs_df["17_LI_hh_dif"],0)
needs_df["18_LI_hh_ex"]=np.where(needs_df["18_LI_hh_dif"]>0,needs_df["18_LI_hh_dif"],0)

needs_df["15_MoI_hh_ex"]=np.where(needs_df["15_MoI_hh_dif"]>0,needs_df["15_MoI_hh_dif"],0)
needs_df["16_MoI_hh_ex"]=np.where(needs_df["16_MoI_hh_dif"]>0,needs_df["16_MoI_hh_dif"],0)
needs_df["17_MoI_hh_ex"]=np.where(needs_df["17_MoI_hh_dif"]>0,needs_df["17_MoI_hh_dif"],0)
needs_df["18_MoI_hh_ex"]=np.where(needs_df["18_MoI_hh_dif"]>0,needs_df["18_MoI_hh_dif"],0)

needs_df["15_HI_hh_ex"]=np.where(needs_df["15_HI_hh_dif"]>0,needs_df["15_HI_hh_dif"],0)
needs_df["16_HI_hh_ex"]=np.where(needs_df["16_HI_hh_dif"]>0,needs_df["16_HI_hh_dif"],0)
needs_df["17_HI_hh_ex"]=np.where(needs_df["17_HI_hh_dif"]>0,needs_df["17_HI_hh_dif"],0)
needs_df["18_HI_hh_ex"]=np.where(needs_df["18_HI_hh_dif"]>0,needs_df["18_HI_hh_dif"],0)

needs_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.60          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [150]:
needs_df[needs_df.Place=="San Jose city, CA"]

Place  14_HI_hh_count  14_LI_hh_count  14_MoI_hh_count  \
136  San Jose city, CA       113236.43        56270.04         57361.43   

     14_VLI_hh_count  15_HI_hh_count  15_LI_hh_count  15_MoI_hh_count  \
136         80021.86       129444.31        47568.38         54909.17   

     15_VLI_hh_count  16_HI_hh_count  16_LI_hh_count  16_MoI_hh_count  \
136         84434.94       136717.76        39499.75         53250.73   

     16_VLI_hh_count  17_HI_hh_count  17_LI_hh_count  17_MoI_hh_count  \
136         81086.31       139441.72        35856.78         62353.57   

     17_VLI_hh_count  18_HI_hh_count  18_LI_hh_count  18_MoI_hh_count  \
136         76220.17       129372.92        35542.69         64508.41   

     18_VLI_hh_count    PUMA       County  Very Low    Low    Mod  Above Mod  \
136         88943.01 8502.00  Santa Clara   1154.12 678.50 773.50    1778.88   

     15_VLI_hh_needs  15_LI_hh_needs  15_MoI_hh_needs  15_HI_hh_needs  \
136         81175.99        56948.54         58134.93       115015.30   

     16_VLI_hh_needs  16_LI_hh_needs  16_MoI_hh_needs  16_HI_hh_needs  \
136         82330.11        57627.04         58908.43       116794.18   

     17_VLI_hh_needs  17_LI_hh_needs  17_MoI_hh_needs  17_HI_hh_needs  \
136         83484.24        58305.54         59681.93       118573.05   

     18_VLI_hh_needs  18_LI_hh_needs  18_MoI_hh_needs  18_HI_hh_needs  \
136         84638.36        58984.04         60455.43       120351.93   

     15_VLI_hh_mod  16_VLI_hh_mod  17_VLI_hh_mod  18_VLI_hh_mod  15_LI_hh_mod  \
136       84434.94       82330.11       83484.24       88943.01      56948.54   

     16_LI_hh_mod  17_LI_hh_mod  18_LI_hh_mod  15_MoI_hh_mod  16_MoI_hh_mod  \
136      57627.04      58305.54      58984.04       58134.93       58908.43   

     17_MoI_hh_mod  18_MoI_hh_mod  15_HI_hh_mod  16_HI_hh_mod  17_HI_hh_mod  \
136       62353.57       64508.41     129444.31     136717.76     139441.72   

     18_HI_hh_mod  15_VLI_hh_dif  16_VLI_hh_dif  17_VLI_hh_dif  18_VLI_hh_dif  \
136     129372.92       -3258.95        1243.80        7264.06       -4304.65   

     15_LI_hh_dif  16_LI_hh_dif  17_LI_hh_dif  18_LI_hh_dif  15_MoI_hh_dif  \
136       9380.16      18127.29      22448.76      23441.34        3225.76   

     16_MoI_hh_dif  17_MoI_hh_dif  18_MoI_hh_dif  15_HI_hh_dif  16_HI_hh_dif  \
136        5657.70       -2671.64       -4052.98     -14429.00     -19923.59   

     17_HI_hh_dif  18_HI_hh_dif  15_VLI_hh_ex  16_VLI_hh_ex  17_VLI_hh_ex  \
136     -20868.66      -9020.99          0.00       1243.80       7264.06   

     18_VLI_hh_ex  15_LI_hh_ex  16_LI_hh_ex  17_LI_hh_ex  18_LI_hh_ex  \
136          0.00      9380.16     18127.29     22448.76     23441.34   

     15_MoI_hh_ex  16_MoI_hh_ex  17_MoI_hh_ex  18_MoI_hh_ex  15_HI_hh_ex  \
136       3225.76       5657.70          0.00          0.00         0.00   

     16_HI_hh_ex  17_HI_hh_ex  18_HI_hh_ex  
136         0.00         0.00         0.00

In [151]:
#calculate remainder hhs by county
sum_df = needs_df.groupby("County").sum()
ex_df=sum_df[["15_VLI_hh_ex",
              "16_VLI_hh_ex",
              "17_VLI_hh_ex",
              "18_VLI_hh_ex",
              "15_LI_hh_ex",
              "16_LI_hh_ex",
              "17_LI_hh_ex",
              "18_LI_hh_ex",
              "15_MoI_hh_ex",
              "16_MoI_hh_ex",
              "17_MoI_hh_ex",
              "18_MoI_hh_ex",
              "15_HI_hh_ex",
              "16_HI_hh_ex",
              "17_HI_hh_ex",
              "18_HI_hh_ex",]]
ex_df

15_VLI_hh_ex  16_VLI_hh_ex  17_VLI_hh_ex  18_VLI_hh_ex  \
County                                                                  
Alameda            15089.66      20050.40      26438.17      16967.34   
Contra Costa        4338.71      10835.49       6189.51       4466.14   
El Dorado              0.00          0.00          0.00          0.00   
Fresno                 0.00          0.00          0.00          0.00   
Marin                  0.00          0.00        878.36        772.73   
Mendocino              0.00          0.00          0.00          0.00   
Merced                 0.00          0.00          0.00          0.00   
Monterey               0.00          0.00          0.00          0.00   
Napa                1722.78       2414.67       4405.69       3368.67   
Placer                 0.00          0.00          0.00          0.00   
Sacramento             0.00          0.00          0.00          0.00   
San Francisco       1811.25       8871.50       8221.75          0.00   
San Joaquin            0.00          0.00          0.00          0.00   
San Mateo           2482.65       5375.78       4939.39       6337.69   
Santa Clara         5785.69       5503.33      10885.06       5436.09   
Santa Cruz             0.00          0.00          0.00          0.00   
Solano              2327.54       5241.51       6453.63      14538.50   
Sonoma              6528.09      12561.16       7567.71       2919.70   
Stanislaus             0.00          0.00          0.00          0.00   
Yolo                   0.00          0.00          0.00          0.00   

               15_LI_hh_ex  16_LI_hh_ex  17_LI_hh_ex  18_LI_hh_ex  \
County                                                              
Alameda             122.93        46.88       370.35       109.25   
Contra Costa       1295.34      1790.88      3815.04      3409.59   
El Dorado             0.00         0.00         0.00         0.00   
Fresno                0.00         0.00         0.00         0.00   
Marin              4507.66      4090.07      3329.34      2943.63   
Mendocino             0.00         0.00         0.00         0.00   
Merced                0.00         0.00         0.00         0.00   
Monterey              0.00         0.00         0.00         0.00   
Napa                  0.00       278.34       275.55       693.73   
Placer                0.00         0.00         0.00         0.00   
Sacramento            0.00         0.00         0.00         0.00   
San Francisco      2579.88      3461.75      6137.62      3001.50   
San Joaquin           0.00         0.00         0.00         0.00   
San Mateo          1792.69      1156.99       721.46       325.51   
Santa Clara       16299.61     27362.13     38630.69     37813.22   
Santa Cruz            0.00         0.00         0.00         0.00   
Solano              478.34      2136.50      1258.71       748.52   
Sonoma              730.89      2056.41      4213.95       932.48   
Stanislaus            0.00         0.00         0.00         0.00   
Yolo                  0.00         0.00         0.00         0.00   

               15_MoI_hh_ex  16_MoI_hh_ex  17_MoI_hh_ex  18_MoI_hh_ex  \
County                                                                  
Alameda            24913.23      32787.20      39840.40      55023.10   
Contra Costa       10350.16      21781.88      23059.00      29320.08   
El Dorado              0.00          0.00          0.00          0.00   
Fresno                 0.00          0.00          0.00          0.00   
Marin                165.70       2049.66       1276.45       4397.56   
Mendocino              0.00          0.00          0.00          0.00   
Merced                 0.00          0.00          0.00          0.00   
Monterey               0.00          0.00          0.00          0.00   
Napa                 915.99       1194.66          0.00       1706.96   
Placer                 0.00          0.00          0.00          0.00   
Sacramento   

## Part B3. Bring in move data and create weights for reallocation of hhs

In [152]:
#import movers by city/county
move_df=pd.read_csv("Migration Analysis/bay_movers_by_city.csv", delimiter=",")
move_df

Unnamed: 0                        Place  Alameda  Contra Costa   Marin  \
0            0             Alameda city, CA  5305.05        508.50   18.06   
1            1              Albany city, CA  2048.06        200.38   34.78   
2            3     American Canyon city, CA    10.36         20.60   24.09   
3            7           Belvedere city, CA    11.81         10.16  129.23   
4            8             Benicia city, CA   453.60        598.60   29.00   
5            9            Berkeley city, CA 12792.94       1251.62  217.22   
6           12           Calistoga city, CA     3.99          7.94    9.28   
7           13            Capitola city, CA    94.95         42.22   18.93   
8           16      Citrus Heights city, CA     0.18          0.33    0.11   
9           18          Cloverdale city, CA     6.96          4.28   16.64   
10          19               Colma town, CA     3.26          1.88    0.29   
11          21             Concord city, CA   292.82       3263.90    3.02   
12          23        Corte Madera town, CA    45.76         39.37  500.77   
13          24              Cotati city, CA    23.23          7.00  108.97   
14          26           Daly City city, CA   173.81        100.32   15.34   
15          27            Danville town, CA    46.20        211.68    3.53   
16          28               Davis city, CA   436.77        160.77   93.50   
17          29               Dixon city, CA    13.52        146.64   27.04   
18          31              Dublin city, CA  3436.54        343.57   42.39   
19          33          El Cerrito city, CA   682.92       1365.63   39.48   
20          34          Emeryville city, CA  1257.32        141.95   17.26   
21          35             Escalon city, CA    16.92         24.75    0.85   
22          37             Fairfax town, CA    13.28         11.43  145.39   
23          38           Fairfield city, CA   445.19        645.33  387.35   
24          39          Fort Bragg city, CA    19.78          2.02    8.44   
25          44             Hayward city, CA  8914.69        448.17   55.87   
26          47          Healdsburg city, CA     9.74          5.99   23.30   
27          48            Hercules city, CA   537.29       1318.87   29.79   
28          51           Lafayette city, CA   306.90       1406.16   23.44   
29          53            Larkspur city, CA    73.06         62.87  799.62   
..         ...                          ...      ...           ...     ...   
70         126            Stockton city, CA     9.40         13.75    0.47   
71         127         Suisun City city, CA   112.91        163.66   98.24   
72         130             Tiburon town, CA    45.76         39.37  500.77   
73         131               Tracy city, CA  1442.38        400.75    9.52   
74         134               Ukiah city, CA    40.51          4.13   17.29   
75         135       Unincorporated_Alameda  7394.45        551.45    9.92   
76         138  Unincorporated_Contra Costa  1379.55       5625.81   74.83   
77         140     Unincorporated_El Dorado   381.02        395.76  243.66   
78         142         Unincorporated_Marin   169.00        145.42 1849.63   
79         143     Unincorporated_Mendocino   196.07         19.98   83.67   
80         144          Unincorporated_Napa    21.47         42.71   49.95   
81         146        Unincorporated_Placer    55.40         18.73    3.61   
82         148    Unincorporated_Sacramento   470.09        568.95  164.98   
83         149   Unincorporated_San Joaquin   634.65        371.03   11.41   
84         151     Unincorporated_San Mateo    11.15          6.44    0.98   
85         153    Unincorporated_Santa Cruz   442.81        196.91   88.27   
86         154        Unincorporated_Solano    80.84        203.53   41.27   
87         155        Unincorporated_Sonoma   214.67         93.94  553.13   
88         157          Unincorporated_Yolo   141.79         52.19   30.35   
89         158          Un

In [153]:
outer_mask = (move_df["current_county"]=="Sacramento")|(move_df["current_county"]=="San Joaquin")|(move_df["current_county"]=="Stanislaus")|(move_df["current_county"]=="Santa Cruz")|(move_df["current_county"]=="Monterey")|(move_df["current_county"]=="Placer")|(move_df["current_county"]=="Yolo")|(move_df["current_county"]=="Fresno")| (move_df["current_county"]=="Merced")|(move_df["current_county"]=="El Dorado")|(move_df["current_county"]=="San Benito")|(move_df["current_county"]=="Mendocino")
outer_move_df = move_df[outer_mask].copy()
outer_move_df.drop('Unnamed: 0', axis=1, inplace=True)
outer_move_df

Place  Alameda  Contra Costa  Marin   Napa  \
7            Capitola city, CA    94.95         42.22  18.93   3.33   
8      Citrus Heights city, CA     0.18          0.33   0.11   0.04   
16              Davis city, CA   436.77        160.77  93.50  16.90   
21            Escalon city, CA    16.92         24.75   0.85   1.84   
24         Fort Bragg city, CA    19.78          2.02   8.44  18.77   
30            Lathrop city, CA   292.66         81.31   1.93   1.26   
31            Lincoln city, CA    49.27          8.99  10.56  32.84   
33               Lodi city, CA   152.66        223.30   7.71  16.65   
34             Loomis town, CA     7.06          1.29   1.51   4.70   
35            Manteca city, CA  1282.49        356.77   8.48   5.56   
46        Placerville city, CA    25.53         26.52  16.33   5.67   
49        Point Arena city, CA     1.41          0.14   0.60   1.34   
50     Rancho Cordova city, CA    81.51         34.44   9.76   5.17   
53              Ripon city, CA    33.09         48.40   1.67   3.61   
54            Rocklin city, CA    62.62         11.43  13.42  41.75   
56          Roseville city, CA   812.78        293.58  34.93   6.61   
58         Sacramento city, CA  1588.05        894.96 150.04 187.66   
63         Santa Cruz city, CA   376.16        167.27  74.98  13.18   
68   South Lake Tahoe city, CA    83.96         87.21  53.69  18.64   
70           Stockton city, CA     9.40         13.75   0.47   1.02   
73              Tracy city, CA  1442.38        400.75   9.52   6.21   
74              Ukiah city, CA    40.51          4.13  17.29  38.44   
77    Unincorporated_El Dorado   381.02        395.76 243.66  84.58   
79    Unincorporated_Mendocino   196.07         19.98  83.67 186.08   
81       Unincorporated_Placer    55.40         18.73   3.61   5.18   
82   Unincorporated_Sacramento   470.09        568.95 164.98  62.11   
83  Unincorporated_San Joaquin   634.65        371.03  11.41  19.94   
85   Unincorporated_Santa Cruz   442.81        196.91  88.27  15.52   
88         Unincorporated_Yolo   141.79         52.19  30.35   5.49   
93        Watsonville city, CA     0.00          0.00   0.00   0.00   
94    West Sacramento city, CA   315.23        116.03  67.48  12.20   
95            Willits city, CA    12.72          1.30   5.43  12.07   
97            Winters city, CA    39.25         14.45   8.40   1.52   
98           Woodland city, CA   334.22        123.02  71.54  12.94   

    San Francisco  San Mateo  Santa Clara  Solano  Sonoma     PUMA  \
7           38.90      51.17       197.81    8.22    7.18  8702.00   
8            0.19       0.05         0.17    0.39    0.05  6704.00   
16         214.59     158.01       366.74  384.33  109.02 11300.00   
21           5.67       1.30        10.80    0.54    2.56  7704.00   
24           3.65       3.70         3.44    3.78   68.38  3300.00   
30          21.34      13.86       200.34    2.94    3.02  7703.00   
31          22.68      91.10       151.32   37.93   36.75  6102.00   
33          51.16      11.77        97.44    4.87   23.14  7704.00   
34           3.25      13.05        21.67    5.43    5.26  6102.00   
35          93.60      60.75       877.92   12.89   13.30  7703.00   
46           6.55       6.34        61.36    2.29   21.48  1700.00   
49           0.26       0.26         0.25    0.27    4.88  3300.00   
50          32.72       4.59       164.16   67.16   65.44  6702.00   
53          11.09       2.55        21.12    1.06    5.02  7704.00   
54          28.83     115.80       192.34   48.21   46.72  6102.00   
56         242.61     196.35       577.73   44.37   17.94  6101.00   
58         902.58     854.11       680.64 1788.23  342.77  6704.00   
63         154.09     202.70       783.62   32.55   28.43  8702.00   
68          21.55      20.86       201.78    7.52   70.62  1700.00   
70           3.15       0.73         6.00    0.30    1.43  7704.00   
73         105.16      68.31       987.39   14.49   14.90  7703.00   

In [154]:
#create total counts for each county
outer_move_df["Alameda_total"]=outer_move_df["Alameda"].sum()
outer_move_df["Contra Costa_total"]=outer_move_df["Contra Costa"].sum()
outer_move_df["San Francisco_total"]=outer_move_df["San Francisco"].sum()
outer_move_df["Santa Clara_total"]=outer_move_df["Santa Clara"].sum()
outer_move_df["San Mateo_total"]=outer_move_df["San Mateo"].sum()
outer_move_df["Marin_total"]=outer_move_df["Marin"].sum()
outer_move_df["Napa_total"]=outer_move_df["Napa"].sum()
outer_move_df["Sonoma_total"]=outer_move_df["Sonoma"].sum()
outer_move_df["Solano_total"]=outer_move_df["Solano"].sum()
outer_move_df

Place  Alameda  Contra Costa  Marin   Napa  \
7            Capitola city, CA    94.95         42.22  18.93   3.33   
8      Citrus Heights city, CA     0.18          0.33   0.11   0.04   
16              Davis city, CA   436.77        160.77  93.50  16.90   
21            Escalon city, CA    16.92         24.75   0.85   1.84   
24         Fort Bragg city, CA    19.78          2.02   8.44  18.77   
30            Lathrop city, CA   292.66         81.31   1.93   1.26   
31            Lincoln city, CA    49.27          8.99  10.56  32.84   
33               Lodi city, CA   152.66        223.30   7.71  16.65   
34             Loomis town, CA     7.06          1.29   1.51   4.70   
35            Manteca city, CA  1282.49        356.77   8.48   5.56   
46        Placerville city, CA    25.53         26.52  16.33   5.67   
49        Point Arena city, CA     1.41          0.14   0.60   1.34   
50     Rancho Cordova city, CA    81.51         34.44   9.76   5.17   
53              Ripon city, CA    33.09         48.40   1.67   3.61   
54            Rocklin city, CA    62.62         11.43  13.42  41.75   
56          Roseville city, CA   812.78        293.58  34.93   6.61   
58         Sacramento city, CA  1588.05        894.96 150.04 187.66   
63         Santa Cruz city, CA   376.16        167.27  74.98  13.18   
68   South Lake Tahoe city, CA    83.96         87.21  53.69  18.64   
70           Stockton city, CA     9.40         13.75   0.47   1.02   
73              Tracy city, CA  1442.38        400.75   9.52   6.21   
74              Ukiah city, CA    40.51          4.13  17.29  38.44   
77    Unincorporated_El Dorado   381.02        395.76 243.66  84.58   
79    Unincorporated_Mendocino   196.07         19.98  83.67 186.08   
81       Unincorporated_Placer    55.40         18.73   3.61   5.18   
82   Unincorporated_Sacramento   470.09        568.95 164.98  62.11   
83  Unincorporated_San Joaquin   634.65        371.03  11.41  19.94   
85   Unincorporated_Santa Cruz   442.81        196.91  88.27  15.52   
88         Unincorporated_Yolo   141.79         52.19  30.35   5.49   
93        Watsonville city, CA     0.00          0.00   0.00   0.00   
94    West Sacramento city, CA   315.23        116.03  67.48  12.20   
95            Willits city, CA    12.72          1.30   5.43  12.07   
97            Winters city, CA    39.25         14.45   8.40   1.52   
98           Woodland city, CA   334.22        123.02  71.54  12.94   

    San Francisco  San Mateo  Santa Clara  Solano  Sonoma     PUMA  \
7           38.90      51.17       197.81    8.22    7.18  8702.00   
8            0.19       0.05         0.17    0.39    0.05  6704.00   
16         214.59     158.01       366.74  384.33  109.02 11300.00   
21           5.67       1.30        10.80    0.54    2.56  7704.00   
24           3.65       3.70         3.44    3.78   68.38  3300.00   
30          21.34      13.86       200.34    2.94    3.02  7703.00   
31          22.68      91.10       151.32   37.93   36.75  6102.00   
33          51.16      11.77        97.44    4.87   23.14  7704.00   
34           3.25      13.05        21.67    5.43    5.26  6102.00   
35          93.60      60.75       877.92   12.89   13.30  7703.00   
46           6.55       6.34        61.36    2.29   21.48  1700.00   
49           0.26       0.26         0.25    0.27    4.88  3300.00   
50          32.72       4.59       164.16   67.16   65.44  6702.00   
53          11.09       2.55        21.12    1.06    5.02  7704.00   
54          28.83     115.80       192.34   48.21   46.72  6102.00   
56         242.61     196.35       577.73   44.37   17.94  6101.00   
58         902.58     854.11       680.64 1788.23  342.77  6704.00   
63         154.09     202.70       783.62   32.55   28.43  8702.00   
68          21.55      20.86       201.78    7.52   70.62  1700.00   
70           3.15       0.73         6.00    0.30    1.43  7704.00   
73         105.16      68.31       987.39   14.49   14.90  7703.00   

In [155]:
#calculate percentage of movers from each county to each city/county
outer_move_df["Alameda_pct"]=outer_move_df["Alameda"]/outer_move_df["Alameda_total"]
outer_move_df["Contra Costa_pct"]=outer_move_df["Contra Costa"]/outer_move_df["Contra Costa_total"]
outer_move_df["San Francisco_pct"]=outer_move_df["San Francisco"]/outer_move_df["San Francisco_total"]
outer_move_df["Santa Clara_pct"]=outer_move_df["Santa Clara"]/outer_move_df["Santa Clara_total"]
outer_move_df["San Mateo_pct"]=outer_move_df["San Mateo"]/outer_move_df["San Mateo_total"]
outer_move_df["Marin_pct"]=outer_move_df["Marin"]/outer_move_df["Marin_total"]
outer_move_df["Napa_pct"]=outer_move_df["Napa"]/outer_move_df["Napa_total"]
outer_move_df["Sonoma_pct"]=outer_move_df["Sonoma"]/outer_move_df["Sonoma_total"]
outer_move_df["Solano_pct"]=outer_move_df["Solano"]/outer_move_df["Solano_total"]
outer_move_df

Place  Alameda  Contra Costa  Marin   Napa  \
7            Capitola city, CA    94.95         42.22  18.93   3.33   
8      Citrus Heights city, CA     0.18          0.33   0.11   0.04   
16              Davis city, CA   436.77        160.77  93.50  16.90   
21            Escalon city, CA    16.92         24.75   0.85   1.84   
24         Fort Bragg city, CA    19.78          2.02   8.44  18.77   
30            Lathrop city, CA   292.66         81.31   1.93   1.26   
31            Lincoln city, CA    49.27          8.99  10.56  32.84   
33               Lodi city, CA   152.66        223.30   7.71  16.65   
34             Loomis town, CA     7.06          1.29   1.51   4.70   
35            Manteca city, CA  1282.49        356.77   8.48   5.56   
46        Placerville city, CA    25.53         26.52  16.33   5.67   
49        Point Arena city, CA     1.41          0.14   0.60   1.34   
50     Rancho Cordova city, CA    81.51         34.44   9.76   5.17   
53              Ripon city, CA    33.09         48.40   1.67   3.61   
54            Rocklin city, CA    62.62         11.43  13.42  41.75   
56          Roseville city, CA   812.78        293.58  34.93   6.61   
58         Sacramento city, CA  1588.05        894.96 150.04 187.66   
63         Santa Cruz city, CA   376.16        167.27  74.98  13.18   
68   South Lake Tahoe city, CA    83.96         87.21  53.69  18.64   
70           Stockton city, CA     9.40         13.75   0.47   1.02   
73              Tracy city, CA  1442.38        400.75   9.52   6.21   
74              Ukiah city, CA    40.51          4.13  17.29  38.44   
77    Unincorporated_El Dorado   381.02        395.76 243.66  84.58   
79    Unincorporated_Mendocino   196.07         19.98  83.67 186.08   
81       Unincorporated_Placer    55.40         18.73   3.61   5.18   
82   Unincorporated_Sacramento   470.09        568.95 164.98  62.11   
83  Unincorporated_San Joaquin   634.65        371.03  11.41  19.94   
85   Unincorporated_Santa Cruz   442.81        196.91  88.27  15.52   
88         Unincorporated_Yolo   141.79         52.19  30.35   5.49   
93        Watsonville city, CA     0.00          0.00   0.00   0.00   
94    West Sacramento city, CA   315.23        116.03  67.48  12.20   
95            Willits city, CA    12.72          1.30   5.43  12.07   
97            Winters city, CA    39.25         14.45   8.40   1.52   
98           Woodland city, CA   334.22        123.02  71.54  12.94   

    San Francisco  San Mateo  Santa Clara  Solano  Sonoma     PUMA  \
7           38.90      51.17       197.81    8.22    7.18  8702.00   
8            0.19       0.05         0.17    0.39    0.05  6704.00   
16         214.59     158.01       366.74  384.33  109.02 11300.00   
21           5.67       1.30        10.80    0.54    2.56  7704.00   
24           3.65       3.70         3.44    3.78   68.38  3300.00   
30          21.34      13.86       200.34    2.94    3.02  7703.00   
31          22.68      91.10       151.32   37.93   36.75  6102.00   
33          51.16      11.77        97.44    4.87   23.14  7704.00   
34           3.25      13.05        21.67    5.43    5.26  6102.00   
35          93.60      60.75       877.92   12.89   13.30  7703.00   
46           6.55       6.34        61.36    2.29   21.48  1700.00   
49           0.26       0.26         0.25    0.27    4.88  3300.00   
50          32.72       4.59       164.16   67.16   65.44  6702.00   
53          11.09       2.55        21.12    1.06    5.02  7704.00   
54          28.83     115.80       192.34   48.21   46.72  6102.00   
56         242.61     196.35       577.73   44.37   17.94  6101.00   
58         902.58     854.11       680.64 1788.23  342.77  6704.00   
63         154.09     202.70       783.62   32.55   28.43  8702.00   
68          21.55      20.86       201.78    7.52   70.62  1700.00   
70           3.15       0.73         6.00    0.30    1.43  7704.00   
73         105.16      68.31       987.39   14.49   14.90  7703.00   

## Part B4. Reallocate hhs using move weights

In [156]:
weights_df = outer_move_df[["Place","Alameda_pct","Contra Costa_pct","San Francisco_pct","Santa Clara_pct","San Mateo_pct","Marin_pct","Napa_pct","Sonoma_pct","Solano_pct"]].copy()
weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [157]:
#bring over Alameda County reallocated units
weights_df["15_VLI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","15_VLI_hh_ex"]
weights_df["16_VLI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","16_VLI_hh_ex"]
weights_df["17_VLI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","17_VLI_hh_ex"]
weights_df["18_VLI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","18_VLI_hh_ex"]

weights_df["15_LI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","15_LI_hh_ex"]
weights_df["16_LI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","16_LI_hh_ex"]
weights_df["17_LI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","17_LI_hh_ex"]
weights_df["18_LI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","18_LI_hh_ex"]

weights_df["15_MoI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","15_MoI_hh_ex"]
weights_df["16_MoI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","16_MoI_hh_ex"]
weights_df["17_MoI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","17_MoI_hh_ex"]
weights_df["18_MoI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","18_MoI_hh_ex"]

weights_df["15_HI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","15_HI_hh_ex"]
weights_df["16_HI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","16_HI_hh_ex"]
weights_df["17_HI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","17_HI_hh_ex"]
weights_df["18_HI_ex_Alameda"]=weights_df["Alameda_pct"]*ex_df.loc["Alameda","18_HI_hh_ex"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [158]:
#bring over Contra Costa County reallocated units
weights_df["15_VLI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","15_VLI_hh_ex"]
weights_df["16_VLI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","16_VLI_hh_ex"]
weights_df["17_VLI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","17_VLI_hh_ex"]
weights_df["18_VLI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","18_VLI_hh_ex"]

weights_df["15_LI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","15_LI_hh_ex"]
weights_df["16_LI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","16_LI_hh_ex"]
weights_df["17_LI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","17_LI_hh_ex"]
weights_df["18_LI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","18_LI_hh_ex"]

weights_df["15_MoI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","15_MoI_hh_ex"]
weights_df["16_MoI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","16_MoI_hh_ex"]
weights_df["17_MoI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","17_MoI_hh_ex"]
weights_df["18_MoI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","18_MoI_hh_ex"]

weights_df["15_HI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","15_HI_hh_ex"]
weights_df["16_HI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","16_HI_hh_ex"]
weights_df["17_HI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","17_HI_hh_ex"]
weights_df["18_HI_ex_Contra Costa"]=weights_df["Contra Costa_pct"]*ex_df.loc["Contra Costa","18_HI_hh_ex"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [159]:
#bring over San Francisco County reallocated units
weights_df["15_VLI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","15_VLI_hh_ex"]
weights_df["16_VLI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","16_VLI_hh_ex"]
weights_df["17_VLI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","17_VLI_hh_ex"]
weights_df["18_VLI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","18_VLI_hh_ex"]

weights_df["15_LI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","15_LI_hh_ex"]
weights_df["16_LI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","16_LI_hh_ex"]
weights_df["17_LI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","17_LI_hh_ex"]
weights_df["18_LI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","18_LI_hh_ex"]

weights_df["15_MoI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","15_MoI_hh_ex"]
weights_df["16_MoI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","16_MoI_hh_ex"]
weights_df["17_MoI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","17_MoI_hh_ex"]
weights_df["18_MoI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","18_MoI_hh_ex"]

weights_df["15_HI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","15_HI_hh_ex"]
weights_df["16_HI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","16_HI_hh_ex"]
weights_df["17_HI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","17_HI_hh_ex"]
weights_df["18_HI_ex_San Francisco"]=weights_df["San Francisco_pct"]*ex_df.loc["San Francisco","18_HI_hh_ex"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [160]:
#bring over Santa Clara County reallocated units
weights_df["15_VLI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","15_VLI_hh_ex"]
weights_df["16_VLI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","16_VLI_hh_ex"]
weights_df["17_VLI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","17_VLI_hh_ex"]
weights_df["18_VLI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","18_VLI_hh_ex"]

weights_df["15_LI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","15_LI_hh_ex"]
weights_df["16_LI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","16_LI_hh_ex"]
weights_df["17_LI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","17_LI_hh_ex"]
weights_df["18_LI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","18_LI_hh_ex"]

weights_df["15_MoI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","15_MoI_hh_ex"]
weights_df["16_MoI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","16_MoI_hh_ex"]
weights_df["17_MoI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","17_MoI_hh_ex"]
weights_df["18_MoI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","18_MoI_hh_ex"]

weights_df["15_HI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","15_HI_hh_ex"]
weights_df["16_HI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","16_HI_hh_ex"]
weights_df["17_HI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","17_HI_hh_ex"]
weights_df["18_HI_ex_Santa Clara"]=weights_df["Santa Clara_pct"]*ex_df.loc["Santa Clara","18_HI_hh_ex"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [161]:
#bring over San Mateo County reallocated units
weights_df["15_VLI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","15_VLI_hh_ex"]
weights_df["16_VLI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","16_VLI_hh_ex"]
weights_df["17_VLI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","17_VLI_hh_ex"]
weights_df["18_VLI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","18_VLI_hh_ex"]

weights_df["15_LI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","15_LI_hh_ex"]
weights_df["16_LI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","16_LI_hh_ex"]
weights_df["17_LI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","17_LI_hh_ex"]
weights_df["18_LI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","18_LI_hh_ex"]

weights_df["15_MoI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","15_MoI_hh_ex"]
weights_df["16_MoI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","16_MoI_hh_ex"]
weights_df["17_MoI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","17_MoI_hh_ex"]
weights_df["18_MoI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","18_MoI_hh_ex"]

weights_df["15_HI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","15_HI_hh_ex"]
weights_df["16_HI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","16_HI_hh_ex"]
weights_df["17_HI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","17_HI_hh_ex"]
weights_df["18_HI_ex_San Mateo"]=weights_df["San Mateo_pct"]*ex_df.loc["San Mateo","18_HI_hh_ex"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [162]:
#bring over Sonoma County reallocated units
weights_df["15_VLI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","15_VLI_hh_ex"]
weights_df["16_VLI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","16_VLI_hh_ex"]
weights_df["17_VLI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","17_VLI_hh_ex"]
weights_df["18_VLI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","18_VLI_hh_ex"]

weights_df["15_LI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","15_LI_hh_ex"]
weights_df["16_LI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","16_LI_hh_ex"]
weights_df["17_LI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","17_LI_hh_ex"]
weights_df["18_LI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","18_LI_hh_ex"]

weights_df["15_MoI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","15_MoI_hh_ex"]
weights_df["16_MoI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","16_MoI_hh_ex"]
weights_df["17_MoI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","17_MoI_hh_ex"]
weights_df["18_MoI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","18_MoI_hh_ex"]

weights_df["15_HI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","15_HI_hh_ex"]
weights_df["16_HI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","16_HI_hh_ex"]
weights_df["17_HI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","17_HI_hh_ex"]
weights_df["18_HI_ex_Sonoma"]=weights_df["Sonoma_pct"]*ex_df.loc["Sonoma","18_HI_hh_ex"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [163]:
#bring over Napa County reallocated units
weights_df["15_VLI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","15_VLI_hh_ex"]
weights_df["16_VLI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","16_VLI_hh_ex"]
weights_df["17_VLI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","17_VLI_hh_ex"]
weights_df["18_VLI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","18_VLI_hh_ex"]

weights_df["15_LI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","15_LI_hh_ex"]
weights_df["16_LI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","16_LI_hh_ex"]
weights_df["17_LI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","17_LI_hh_ex"]
weights_df["18_LI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","18_LI_hh_ex"]

weights_df["15_MoI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","15_MoI_hh_ex"]
weights_df["16_MoI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","16_MoI_hh_ex"]
weights_df["17_MoI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","17_MoI_hh_ex"]
weights_df["18_MoI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","18_MoI_hh_ex"]

weights_df["15_HI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","15_HI_hh_ex"]
weights_df["16_HI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","16_HI_hh_ex"]
weights_df["17_HI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","17_HI_hh_ex"]
weights_df["18_HI_ex_Napa"]=weights_df["Napa_pct"]*ex_df.loc["Napa","18_HI_hh_ex"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [164]:
#bring over Marin County reallocated units
weights_df["15_VLI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","15_VLI_hh_ex"]
weights_df["16_VLI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","16_VLI_hh_ex"]
weights_df["17_VLI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","17_VLI_hh_ex"]
weights_df["18_VLI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","18_VLI_hh_ex"]

weights_df["15_LI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","15_LI_hh_ex"]
weights_df["16_LI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","16_LI_hh_ex"]
weights_df["17_LI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","17_LI_hh_ex"]
weights_df["18_LI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","18_LI_hh_ex"]

weights_df["15_MoI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","15_MoI_hh_ex"]
weights_df["16_MoI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","16_MoI_hh_ex"]
weights_df["17_MoI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","17_MoI_hh_ex"]
weights_df["18_MoI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","18_MoI_hh_ex"]

weights_df["15_HI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","15_HI_hh_ex"]
weights_df["16_HI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","16_HI_hh_ex"]
weights_df["17_HI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","17_HI_hh_ex"]
weights_df["18_HI_ex_Marin"]=weights_df["Marin_pct"]*ex_df.loc["Marin","18_HI_hh_ex"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [165]:
#bring over Solano County reallocated units
weights_df["15_VLI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","15_VLI_hh_ex"]
weights_df["16_VLI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","16_VLI_hh_ex"]
weights_df["17_VLI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","17_VLI_hh_ex"]
weights_df["18_VLI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","18_VLI_hh_ex"]

weights_df["15_LI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","15_LI_hh_ex"]
weights_df["16_LI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","16_LI_hh_ex"]
weights_df["17_LI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","17_LI_hh_ex"]
weights_df["18_LI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","18_LI_hh_ex"]

weights_df["15_MoI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","15_MoI_hh_ex"]
weights_df["16_MoI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","16_MoI_hh_ex"]
weights_df["17_MoI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","17_MoI_hh_ex"]
weights_df["18_MoI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","18_MoI_hh_ex"]

weights_df["15_HI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","15_HI_hh_ex"]
weights_df["16_HI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","16_HI_hh_ex"]
weights_df["17_HI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","17_HI_hh_ex"]
weights_df["18_HI_ex_Solano"]=weights_df["Solano_pct"]*ex_df.loc["Solano","18_HI_hh_ex"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [166]:
##aggregate units from all 9 Bay Area counties (shifting income levels up to account for difference in AMIs)
weights_df["15_LI_ex"]=weights_df["15_VLI_ex_Alameda"]+weights_df["15_VLI_ex_Contra Costa"]+weights_df["15_VLI_ex_San Francisco"]+weights_df["15_VLI_ex_San Mateo"]+weights_df["15_VLI_ex_Santa Clara"]+weights_df["15_VLI_ex_Sonoma"]+weights_df["15_VLI_ex_Solano"]+weights_df["15_VLI_ex_Napa"]+weights_df["15_VLI_ex_Marin"]
weights_df["16_LI_ex"]=weights_df["16_VLI_ex_Alameda"]+weights_df["16_VLI_ex_Contra Costa"]+weights_df["16_VLI_ex_San Francisco"]+weights_df["16_VLI_ex_San Mateo"]+weights_df["16_VLI_ex_Santa Clara"]+weights_df["16_VLI_ex_Sonoma"]+weights_df["16_VLI_ex_Solano"]+weights_df["16_VLI_ex_Napa"]+weights_df["16_VLI_ex_Marin"]
weights_df["17_LI_ex"]=weights_df["17_VLI_ex_Alameda"]+weights_df["17_VLI_ex_Contra Costa"]+weights_df["17_VLI_ex_San Francisco"]+weights_df["17_VLI_ex_San Mateo"]+weights_df["17_VLI_ex_Santa Clara"]+weights_df["17_VLI_ex_Sonoma"]+weights_df["17_VLI_ex_Solano"]+weights_df["17_VLI_ex_Napa"]+weights_df["17_VLI_ex_Marin"]
weights_df["18_LI_ex"]=weights_df["18_VLI_ex_Alameda"]+weights_df["18_VLI_ex_Contra Costa"]+weights_df["18_VLI_ex_San Francisco"]+weights_df["18_VLI_ex_San Mateo"]+weights_df["18_VLI_ex_Santa Clara"]+weights_df["18_VLI_ex_Sonoma"]+weights_df["18_VLI_ex_Solano"]+weights_df["18_VLI_ex_Napa"]+weights_df["18_VLI_ex_Marin"]

weights_df["15_MoI_ex"]=weights_df["15_LI_ex_Alameda"]+weights_df["15_LI_ex_Contra Costa"]+weights_df["15_LI_ex_San Francisco"]+weights_df["15_LI_ex_San Mateo"]+weights_df["15_LI_ex_Santa Clara"]+weights_df["15_LI_ex_Sonoma"]+weights_df["15_LI_ex_Solano"]+weights_df["15_LI_ex_Napa"]+weights_df["15_LI_ex_Marin"]
weights_df["16_MoI_ex"]=weights_df["16_LI_ex_Alameda"]+weights_df["16_LI_ex_Contra Costa"]+weights_df["16_LI_ex_San Francisco"]+weights_df["16_LI_ex_San Mateo"]+weights_df["16_LI_ex_Santa Clara"]+weights_df["16_LI_ex_Sonoma"]+weights_df["16_LI_ex_Solano"]+weights_df["16_LI_ex_Napa"]+weights_df["16_LI_ex_Marin"]
weights_df["17_MoI_ex"]=weights_df["17_LI_ex_Alameda"]+weights_df["17_LI_ex_Contra Costa"]+weights_df["17_LI_ex_San Francisco"]+weights_df["17_LI_ex_San Mateo"]+weights_df["17_LI_ex_Santa Clara"]+weights_df["17_LI_ex_Sonoma"]+weights_df["17_LI_ex_Solano"]+weights_df["17_LI_ex_Napa"]+weights_df["17_LI_ex_Marin"]
weights_df["18_MoI_ex"]=weights_df["18_LI_ex_Alameda"]+weights_df["18_LI_ex_Contra Costa"]+weights_df["18_LI_ex_San Francisco"]+weights_df["18_LI_ex_San Mateo"]+weights_df["18_LI_ex_Santa Clara"]+weights_df["18_LI_ex_Sonoma"]+weights_df["18_LI_ex_Solano"]+weights_df["18_LI_ex_Napa"]+weights_df["18_LI_ex_Marin"]

weights_df["15_HI_ex"]=weights_df["15_MoI_ex_Alameda"]+weights_df["15_MoI_ex_Contra Costa"]+weights_df["15_MoI_ex_San Francisco"]+weights_df["15_MoI_ex_San Mateo"]+weights_df["15_MoI_ex_Santa Clara"]+weights_df["15_MoI_ex_Sonoma"]+weights_df["15_MoI_ex_Solano"]+weights_df["15_MoI_ex_Napa"]+weights_df["15_MoI_ex_Marin"]+weights_df["15_HI_ex_Alameda"]+weights_df["15_HI_ex_Contra Costa"]+weights_df["15_HI_ex_San Francisco"]+weights_df["15_HI_ex_San Mateo"]+weights_df["15_HI_ex_Santa Clara"]+weights_df["15_HI_ex_Sonoma"]+weights_df["15_HI_ex_Solano"]+weights_df["15_HI_ex_Napa"]+weights_df["15_HI_ex_Marin"]
weights_df["16_HI_ex"]=weights_df["16_MoI_ex_Alameda"]+weights_df["16_MoI_ex_Contra Costa"]+weights_df["16_MoI_ex_San Francisco"]+weights_df["16_MoI_ex_San Mateo"]+weights_df["16_MoI_ex_Santa Clara"]+weights_df["16_MoI_ex_Sonoma"]+weights_df["16_MoI_ex_Solano"]+weights_df["16_MoI_ex_Napa"]+weights_df["16_MoI_ex_Marin"]+weights_df["16_HI_ex_Alameda"]+weights_df["16_HI_ex_Contra Costa"]+weights_df["16_HI_ex_San Francisco"]+weights_df["16_HI_ex_San Mateo"]+weights_df["16_HI_ex_Santa Clara"]+weights_df["16_HI_ex_Sonoma"]+weights_df["16_HI_ex_Solano"]+weights_df["16_HI_ex_Napa"]+weights_df["16_HI_ex_Marin"]
weights_df["17_HI_ex"]=weights_df["17_MoI_ex_Alameda"]+weights_df["17_MoI_ex_Contra Costa"]+weights_df["17_MoI_ex_San Francisco"]+weights_df["17_MoI_ex_San Mateo"]+weights_df["17_MoI_ex_Santa Clara"]+weights_df["17_MoI_ex_Sonoma"]+weights_df["17_MoI_ex_Solano"]+weights_df["17_MoI_ex_Napa"]+weights_df["17_MoI_ex_Marin"]+weights_df["17_HI_ex_Alameda"]+weights_df["17_HI_ex_Contra Costa"]+weights_df["17_HI_ex_San Francisco"]+weights_df["17_HI_ex_San Mateo"]+weights_df["17_HI_ex_Santa Clara"]+weights_df["17_HI_ex_Sonoma"]+weights_df["17_HI_ex_Solano"]+weights_df["17_HI_ex_Napa"]+weights_df["17_HI_ex_Marin"]
weights_df["18_HI_ex"]=weights_df["18_MoI_ex_Alameda"]+weights_df["18_MoI_ex_Contra Costa"]+weights_df["18_MoI_ex_San Francisco"]+weights_df["18_MoI_ex_San Mateo"]+weights_df["18_MoI_ex_Santa Clara"]+weights_df["18_MoI_ex_Sonoma"]+weights_df["18_MoI_ex_Solano"]+weights_df["18_MoI_ex_Napa"]+weights_df["18_MoI_ex_Marin"]+weights_df["18_HI_ex_Alameda"]+weights_df["18_HI_ex_Contra Costa"]+weights_df["18_HI_ex_San Francisco"]+weights_df["18_HI_ex_San Mateo"]+weights_df["18_HI_ex_Santa Clara"]+weights_df["18_HI_ex_Sonoma"]+weights_df["18_HI_ex_Solano"]+weights_df["18_HI_ex_Napa"]+weights_df["18_HI_ex_Marin"]

weights_df

Place  Alameda_pct  Contra Costa_pct  \
7            Capitola city, CA         0.01              0.01   
8      Citrus Heights city, CA         0.00              0.00   
16              Davis city, CA         0.04              0.03   
21            Escalon city, CA         0.00              0.01   
24         Fort Bragg city, CA         0.00              0.00   
30            Lathrop city, CA         0.03              0.02   
31            Lincoln city, CA         0.00              0.00   
33               Lodi city, CA         0.02              0.05   
34             Loomis town, CA         0.00              0.00   
35            Manteca city, CA         0.13              0.07   
46        Placerville city, CA         0.00              0.01   
49        Point Arena city, CA         0.00              0.00   
50     Rancho Cordova city, CA         0.01              0.01   
53              Ripon city, CA         0.00              0.01   
54            Rocklin city, CA         0.01              0.00   
56          Roseville city, CA         0.08              0.06   
58         Sacramento city, CA         0.16              0.19   
63         Santa Cruz city, CA         0.04              0.04   
68   South Lake Tahoe city, CA         0.01              0.02   
70           Stockton city, CA         0.00              0.00   
73              Tracy city, CA         0.15              0.08   
74              Ukiah city, CA         0.00              0.00   
77    Unincorporated_El Dorado         0.04              0.08   
79    Unincorporated_Mendocino         0.02              0.00   
81       Unincorporated_Placer         0.01              0.00   
82   Unincorporated_Sacramento         0.05              0.12   
83  Unincorporated_San Joaquin         0.06              0.08   
85   Unincorporated_Santa Cruz         0.04              0.04   
88         Unincorporated_Yolo         0.01              0.01   
93        Watsonville city, CA         0.00              0.00   
94    West Sacramento city, CA         0.03              0.02   
95            Willits city, CA         0.00              0.00   
97            Winters city, CA         0.00              0.00   
98           Woodland city, CA         0.03              0.03   

    San Francisco_pct  Santa Clara_pct  San Mateo_pct  Marin_pct  Napa_pct  \
7                0.01             0.02           0.02       0.01      0.00   
8                0.00             0.00           0.00       0.00      0.00   
16               0.07             0.04           0.06       0.07      0.02   
21               0.00             0.00           0.00       0.00      0.00   
24               0.00             0.00           0.00       0.01      0.02   
30               0.01             0.02           0.01       0.00      0.00   
31               0.01             0.02           0.03       0.01      0.04   
33               0.02             0.01           0.00       0.01      0.02   
34               0.00             0.00           0.00       0.00      0.01   
35               0.03             0.10           0.02       0.01      0.01   
46               0.00             0.01           0.00       0.01      0.01   
49               0.00             0.00           0.00       0.00      0.00   
50               0.01             0.02           0.00       0.01      0.01   
53               0.00             0.00           0.00       0.00      0.00   
54               0.01             0.02           0.04       0.01      0.05   
56               0.08             0.06           0.07       0.03      0.01   
58               0.28             0.08           0.31       0.11      0.22   
63               0.05             0.09           0.07       0.06      0.02   
68               0.01             0.02           0.01       0.04      0.02   
70               0.00             0.00           0.00       0.00      0.00   
73               0.03             0.11           0.02       0.01      0.01   
74               0.00            

In [167]:
#create a new dataframe with just extra hhs by place
remove_df=weights_df[["Place","15_LI_ex","16_LI_ex","17_LI_ex","18_LI_ex","15_MoI_ex","16_MoI_ex","17_MoI_ex","18_MoI_ex","15_HI_ex","16_HI_ex","17_HI_ex","18_HI_ex"]].copy()
remove_df

Place  15_LI_ex  16_LI_ex  17_LI_ex  18_LI_ex  \
7            Capitola city, CA    407.96    673.40    803.22    501.94   
8      Citrus Heights city, CA      1.28      2.74      2.77      2.58   
16              Davis city, CA   1863.48   3502.88   3778.29   3180.85   
21            Escalon city, CA     70.41    134.43    126.09     74.49   
24         Fort Bragg city, CA    260.74    470.56    394.56    220.86   
30            Lathrop city, CA    683.53   1006.95   1227.30    749.00   
31            Lincoln city, CA    461.42    784.88    900.25    715.96   
33               Lodi city, CA    635.23   1212.85   1137.65    672.03   
34             Loomis town, CA     66.09    112.41    128.94    102.54   
35            Manteca city, CA   2996.08   4414.37   5379.54   3282.98   
46        Placerville city, CA    181.26    308.33    314.46    186.01   
49        Point Arena city, CA     18.62     33.61     28.18     15.78   
50     Rancho Cordova city, CA    506.90    881.91    898.17    637.51   
53              Ripon city, CA    137.69    262.88    246.58    145.66   
54            Rocklin city, CA    586.50    997.66   1144.31    910.06   
56          Roseville city, CA   2273.79   3890.03   4405.24   2697.10   
58         Sacramento city, CA   7313.36  14550.45  15192.43  13907.61   
63         Santa Cruz city, CA   1616.14   2667.70   3181.98   1988.46   
68   South Lake Tahoe city, CA    596.06   1013.95   1034.10    611.70   
70           Stockton city, CA     39.12     74.68     70.05     41.38   
73              Tracy city, CA   3368.82   4962.81   6048.83   3691.49   
74              Ukiah city, CA    533.89    963.52    807.90    452.24   
77    Unincorporated_El Dorado   2704.93   4601.30   4692.74   2775.89   
79    Unincorporated_Mendocino   2584.34   4664.00   3910.72   2189.13   
81       Unincorporated_Placer    202.15    345.18    392.57    264.37   
82   Unincorporated_Sacramento   2580.92   5293.17   5351.78   4331.15   
83  Unincorporated_San Joaquin   1782.26   2923.77   3196.96   1927.09   
85   Unincorporated_Santa Cruz   1902.49   3140.38   3745.78   2340.78   
88         Unincorporated_Yolo    604.96   1137.17   1226.57   1032.62   
93        Watsonville city, CA      0.00      0.00      0.00      0.00   
94    West Sacramento city, CA   1344.94   2528.17   2726.94   2295.74   
95            Willits city, CA    167.62    302.50    253.64    141.98   
97            Winters city, CA    167.44    314.75    339.50    285.82   
98           Woodland city, CA   1425.97   2680.47   2891.21   2434.04   

    15_MoI_ex  16_MoI_ex  17_MoI_ex  18_MoI_ex  15_HI_ex  16_HI_ex  17_HI_ex  \
7      501.41     748.01    1033.11     948.90    895.03   1099.57   1022.51   
8        1.04       1.50       1.91       1.52      2.76      3.54      3.79   
16    1386.57    2070.45    2718.31    2210.67   3698.20   4182.20   4563.24   
21      35.58      54.42      85.11      72.98    143.64    214.87    225.77   
24      62.05     108.29     170.53      80.75    181.04    163.29    249.82   
30     420.31     676.51     986.35     926.26   1323.89   1760.01   1827.49   
31     404.72     618.75     834.30     742.32    806.13    788.89    759.84   
33     321.00     491.02     767.87     658.41   1295.97   1938.59   2036.97   
34      57.96      88.62     119.49     106.32    115.46    112.99    108.83   
35    1842.15    2964.97    4323.02    4059.51   5803.11   7715.30   8011.18   
46     190.02     277.03     378.72     332.02    281.08    377.93    368.85   
49       4.43       7.74      12.18       5.77     12.93     11.66     17.84   
50     396.40     670.41     954.90     805.86    770.24    872.31    918.19   
53      69.58     106.43     166.44     142.71    280.90    420.19    441.51   
54     514.44     786.49    1060.48     943.56   1024.67   1002.75    965.83   
56    1584.40    2355.80    3384.00    2981.20   4951.90   6317.24   6541.62   
58    3613.90    5546.36    7254.64    5417.94  15077.56  16626.98  18878.

In [168]:
# create new dataframe with model estimates and extra hh numbers
mod_df = needs_df[["Place","County",
                     "15_VLI_hh_mod",
                     "16_VLI_hh_mod",
                     "17_VLI_hh_mod",
                     "18_VLI_hh_mod",
                     "15_LI_hh_mod",
                     "16_LI_hh_mod",
                     "17_LI_hh_mod",
                     "18_LI_hh_mod",
                     "15_MoI_hh_mod",
                     "16_MoI_hh_mod",
                     "17_MoI_hh_mod",
                     "18_MoI_hh_mod",
                     "15_HI_hh_mod",
                     "16_HI_hh_mod",
                     "17_HI_hh_mod",
                     "18_HI_hh_mod"]].copy()
mod_df = mod_df.merge(remove_df,how='left',on="Place")
mod_df

Place        County  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

In [169]:
#create a filter for if hh counts are now negative
neg_mask = ((~mod_df["15_LI_ex"].isna())|
            (~mod_df["16_LI_ex"].isna())|
            (~mod_df["17_LI_ex"].isna())|
            (~mod_df["18_LI_ex"].isna())|
            (~mod_df["15_MoI_ex"].isna())|
            (~mod_df["16_MoI_ex"].isna())|
            (~mod_df["17_MoI_ex"].isna())|
            (~mod_df["18_MoI_ex"].isna())|
            (~mod_df["15_HI_ex"].isna())|
            (~mod_df["16_HI_ex"].isna())|
            (~mod_df["17_HI_ex"].isna())|
            (~mod_df["18_HI_ex"].isna()))

In [170]:
mod_df["15_LI_hh_mod"]=np.where(neg_mask,mod_df["15_LI_hh_mod"]-(mod_df["15_LI_ex"]*1),mod_df["15_LI_hh_mod"])
mod_df["16_LI_hh_mod"]=np.where(neg_mask,mod_df["16_LI_hh_mod"]-(mod_df["16_LI_ex"]*1),mod_df["16_LI_hh_mod"])
mod_df["17_LI_hh_mod"]=np.where(neg_mask,mod_df["17_LI_hh_mod"]-(mod_df["17_LI_ex"]*1),mod_df["17_LI_hh_mod"])
mod_df["18_LI_hh_mod"]=np.where(neg_mask,mod_df["18_LI_hh_mod"]-(mod_df["18_LI_ex"]*1),mod_df["18_LI_hh_mod"])

mod_df["15_MoI_hh_mod"]=np.where(neg_mask,mod_df["15_MoI_hh_mod"]-(mod_df["15_MoI_ex"]*1),mod_df["15_MoI_hh_mod"])
mod_df["16_MoI_hh_mod"]=np.where(neg_mask,mod_df["16_MoI_hh_mod"]-(mod_df["16_MoI_ex"]*1),mod_df["16_MoI_hh_mod"])
mod_df["17_MoI_hh_mod"]=np.where(neg_mask,mod_df["17_MoI_hh_mod"]-(mod_df["17_MoI_ex"]*1),mod_df["17_MoI_hh_mod"])
mod_df["18_MoI_hh_mod"]=np.where(neg_mask,mod_df["18_MoI_hh_mod"]-(mod_df["18_MoI_ex"]*1),mod_df["18_MoI_hh_mod"])

mod_df["15_HI_hh_mod"]=np.where(neg_mask,mod_df["15_HI_hh_mod"]-(mod_df["15_HI_ex"]*1),mod_df["15_HI_hh_mod"])
mod_df["16_HI_hh_mod"]=np.where(neg_mask,mod_df["16_HI_hh_mod"]-(mod_df["16_HI_ex"]*1),mod_df["16_HI_hh_mod"])
mod_df["17_HI_hh_mod"]=np.where(neg_mask,mod_df["17_HI_hh_mod"]-(mod_df["17_HI_ex"]*1),mod_df["17_HI_hh_mod"])
mod_df["18_HI_hh_mod"]=np.where(neg_mask,mod_df["18_HI_hh_mod"]-(mod_df["18_HI_ex"]*1),mod_df["18_HI_hh_mod"])
mod_df

Place        County  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

In [171]:
#chance hh numbers to 0 if they are now below 0
mod_df["15_LI_hh_mod"]=np.where(mod_df["15_LI_hh_mod"]<0,0,mod_df["15_LI_hh_mod"])
mod_df["16_LI_hh_mod"]=np.where(mod_df["16_LI_hh_mod"]<0,0,mod_df["16_LI_hh_mod"])
mod_df["17_LI_hh_mod"]=np.where(mod_df["17_LI_hh_mod"]<0,0,mod_df["17_LI_hh_mod"])
mod_df["18_LI_hh_mod"]=np.where(mod_df["18_LI_hh_mod"]<0,0,mod_df["18_LI_hh_mod"])

mod_df["15_MoI_hh_mod"]=np.where(mod_df["15_MoI_hh_mod"]<0,0,mod_df["15_MoI_hh_mod"])
mod_df["16_MoI_hh_mod"]=np.where(mod_df["16_MoI_hh_mod"]<0,0,mod_df["16_MoI_hh_mod"])
mod_df["17_MoI_hh_mod"]=np.where(mod_df["17_MoI_hh_mod"]<0,0,mod_df["17_MoI_hh_mod"])
mod_df["18_MoI_hh_mod"]=np.where(mod_df["18_MoI_hh_mod"]<0,0,mod_df["18_MoI_hh_mod"])

mod_df["15_HI_hh_mod"]=np.where(mod_df["15_HI_hh_mod"]<0,0,mod_df["15_HI_hh_mod"])
mod_df["15_HI_hh_mod"]=np.where(mod_df["15_HI_hh_mod"]<0,0,mod_df["16_HI_hh_mod"])
mod_df["15_HI_hh_mod"]=np.where(mod_df["15_HI_hh_mod"]<0,0,mod_df["17_HI_hh_mod"])
mod_df["15_HI_hh_mod"]=np.where(mod_df["15_HI_hh_mod"]<0,0,mod_df["18_HI_hh_mod"])
mod_df

Place        County  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

In [172]:
#double check there are no negative hh counts
mask = ((mod_df["15_VLI_hh_mod"]<0)|
        (mod_df["16_VLI_hh_mod"]<0)|
        (mod_df["17_VLI_hh_mod"]<0)|
        (mod_df["18_VLI_hh_mod"]<0)|
        (mod_df["15_LI_hh_mod"]<0)|
        (mod_df["16_LI_hh_mod"]<0)|
        (mod_df["17_LI_hh_mod"]<0)|
        (mod_df["18_LI_hh_mod"]<0)|
        (mod_df["15_MoI_hh_mod"]<0)|
        (mod_df["16_MoI_hh_mod"]<0)|
        (mod_df["17_MoI_hh_mod"]<0)|
        (mod_df["18_MoI_hh_mod"]<0)|
        (mod_df["15_HI_hh_mod"]<0)|
        (mod_df["16_HI_hh_mod"]<0)|
        (mod_df["17_HI_hh_mod"]<0)|
        (mod_df["18_HI_hh_mod"]<0))
mod_df[mask]

Empty DataFrame
Columns: [Place, County, 15_VLI_hh_mod, 16_VLI_hh_mod, 17_VLI_hh_mod, 18_VLI_hh_mod, 15_LI_hh_mod, 16_LI_hh_mod, 17_LI_hh_mod, 18_LI_hh_mod, 15_MoI_hh_mod, 16_MoI_hh_mod, 17_MoI_hh_mod, 18_MoI_hh_mod, 15_HI_hh_mod, 16_HI_hh_mod, 17_HI_hh_mod, 18_HI_hh_mod, 15_LI_ex, 16_LI_ex, 17_LI_ex, 18_LI_ex, 15_MoI_ex, 16_MoI_ex, 17_MoI_ex, 18_MoI_ex, 15_HI_ex, 16_HI_ex, 17_HI_ex, 18_HI_ex]
Index: []

In [173]:
final_needs_df = mod_df[["Place","County",
                         "15_VLI_hh_mod","16_VLI_hh_mod","17_VLI_hh_mod","18_VLI_hh_mod",
                         "15_LI_hh_mod","16_LI_hh_mod","17_LI_hh_mod","18_LI_hh_mod",
                         "15_MoI_hh_mod","16_MoI_hh_mod","17_MoI_hh_mod","18_MoI_hh_mod",
                         "15_HI_hh_mod","16_HI_hh_mod","17_HI_hh_mod","18_HI_hh_mod",]].copy()
final_needs_df

Place        County  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

In [179]:
#export final "needs" model
final_needs_df.to_csv("needs_hh_by_city_and_county.csv")